In [1]:
import fitz
import re
from anytree import Node, RenderTree
import json

# Open the PDF file
pdf_path = "source_pdf/CCAR-121R7《大型飞机公共航空运输承运人运行合格审定规则》.pdf"
doc = fitz.open(pdf_path)

# 构建结构树
root = Node('CCAR-121-R7')
root.title = "大型飞机公共航空运输承运人运行合格审定规则"

# Skip the first 15 pages
start_page = 16
end_page = 243

sections = {}
current_chapter = None  # 章 A章
current_section = None  # 条 第 121.21 条
current_unit = None     # 单元, (a)
current_item = None     # 项，(1)
current_roman = None    # 罗马数字，(i)

# 记录当前节 标题行号
current_section_title_row = 0

chapter_patterns = [re.compile(r'^\s*([A-Z]) 章(.*)'), re.compile(r'([A-Z])章(.*)')]
section_patterns = [re.compile(r'^\s*第\s*(\d+\.\d+)\s*条\s*(.*)')]
unit_patterns = [re.compile(r'^\s*[（(]([a-z])[）)](.*)')]
item_patterns = [re.compile(r'^\s*[（(](\d+)[）)](.*)')]
roman_patterns = [re.compile(r'^\s*[（(]([ivx]+)[）)](.*)')]
header_footer_patterns = [re.compile(r'^\s*(大型飞机公共航空运输承运人运行合格审定规则|-\d+-)\s*$')]

#匹配正则表达式
def match_pattern(line, patterns):
    matched = False
    pattern_matched = None
    for reg in patterns:
        pattern_matched = reg.match(line)
        if pattern_matched:
            matched = True
            break
    return matched, pattern_matched

# Function to clean headers and footers
def clean_header_footer(page_text):
    clean_lines = []
    for line in page_text.split('\n'):
        matched = False
        for reg in header_footer_patterns:
            if reg.match(line):
                matched = True
                break
        if not matched:
            clean_lines.append(line)
    return "\n".join(clean_lines)

# 函数来检查是否有加粗属性
def is_bold(span):
    font_flags = span['flags']
    # font_flags 的 1 位表示 bold
    return font_flags & 1 == 1 

# 识别一页里是否有加粗的行，并且返回加粗的行
def bold_lines_in_page(page_blocks):
    bold_lines = []
    for block in page_blocks:
        if block["type"] != 0:  # 仅处理文本块
            continue
        for line in block["lines"]:
            line_text = ""
            for span in line["spans"]:
                print(span)
                if is_bold(span):
                    bold_lines.append(span["text"])
    return bold_lines

# 函数将树形结构转换为字典，并包含自定义字段
def node_to_dict(node):
    return {
        "name": node.name,
        "title": getattr(node, "title", ""),
        "text": getattr(node, "text", ""),
        "children": [node_to_dict(child) for child in node.children]
    }

# 获取当前节点的前一个同级节点
def get_previous_sibling(node):
    siblings = node.parent.children
    index = siblings.index(node)
    if index > 0:
        return siblings[index - 1]
    return None

# Iterate through the pages and extract text
for page_num in range(start_page - 1, end_page):
# for page_num in range(109 - 1, 109):
    page = doc.load_page(page_num)
    page_text = page.get_text("text")
    blocks = page.get_text("dict")["blocks"]
    cleaned_page_text = clean_header_footer(page_text)
    
    for line in cleaned_page_text.split('\n'):
        line = line.strip()
        if line == '':
            continue
        # print(line)
        # 匹配新章，eg：B运行合格审定的一般规定
        chapter_matched, chapter_matches = match_pattern(line, chapter_patterns)
        if chapter_matched:
            chapter_num = chapter_matches.group(1).strip()
            chapter_title = chapter_matches.group(2).strip()
            current_chapter = Node(chapter_num, parent = root, title = chapter_title, text = [], lv=1)

            # 开始新的章，重置子节点
            current_section = None
            current_unit = None
            current_item = None
            current_roman = None

            # 跳过后续处理，进入下一行循环
            continue

        # 匹配新条款， eg：第121.31条
        section_matched, section_matches = match_pattern(line, section_patterns)
        if section_matched and current_chapter != None:
            section_num = section_matches.group(1).strip()
            section_title = section_matches.group(2).strip()

            section_num1 = int(section_num.split('.')[0])
            section_num2 = int(section_num.split('.')[1])
            current_section_num2 = int(current_section.name.split('.')[1]) if current_section is not None else None
            # if section_num1 == 121 and section_num2 == 367:
            #     print(f"==============>{section_num1}, {section_num2}, {current_section_num2}")
            # 判断是否为被正确提取的条
            if current_section is None \
                or (',' not in section_title and '，' not in section_title and ';' not in section_title and '；' not in section_title and '。' not in section_title and \
                    section_num1 == 121 and section_num2 > current_section_num2  and section_num2 - current_section_num2 <= 100 ):
                current_section = Node(section_num, parent = current_chapter, title = section_title, text = [])
                # 节 标题行号重置为1
                current_section_title_row = 1
    
                # 开始新的条，重置子节点
                current_unit = None
                current_item = None
                current_roman = None
    
                # 跳过后续处理，进入下一行循环
                continue
        
        # 匹配新单元，eg：(a)
        unit_matched, unit_matches = match_pattern(line, unit_patterns)
        if unit_matched and current_section != None:
            unit_num = unit_matches.group(1).strip()
            unit_text = unit_matches.group(2).strip()
            # 需要区分 unit 里的 (i) 和罗马数字的 (i)，主要看当前的编号和前面的编号是否相连
            # 这里有bug，unit为h，后续(1/2...), 其中包含(i)会解析出错
            if unit_num == 'a' or (current_unit != None and (ord(unit_num) - ord(current_unit.name) == 1)):
                current_unit = Node(unit_num, parent = current_section, text = [unit_text])
            
                # 开始新的单元，重置子节点
                current_item = None
                current_roman = None

                # 跳过后续处理，进入下一行循环
                continue

        # 匹配新项，eg：(1)
        item_matched, item_matches = match_pattern(line, item_patterns)
        if item_matched and current_unit != None:
            item_num = item_matches.group(1).strip()
            item_text = item_matches.group(2).strip()
            current_item = Node(item_num, parent = current_unit, text = [item_text])
            
            # 开始新的单元，重置子节点
            current_roman = None

            # 跳过后续处理，进入下一行循环
            continue
        
        # 匹配罗马数字，eg：(i)
        roman_matched, roman_matches = match_pattern(line, roman_patterns)
        if roman_matched and current_item != None:
            roman_num = roman_matches.group(1).strip()
            roman_text = roman_matches.group(2).strip()
            current_roman = Node(roman_num, parent = current_item, text = [roman_text])

            # 跳过后续处理，进入下一行循环
            continue

        # 本行无匹配
        if current_roman != None:
            current_roman.text.append(line)
        elif current_item != None:
            current_item.text.append(line)
        elif current_unit != None:
            current_unit.text.append(line)
        elif current_section != None:
            # 判断是否为第二行标题内容 还是 正文内容 (假设最多只有两行标题)
            if current_section_title_row == 1 and len(line) <= 20 and ',' not in line and '，' not in line and ';' not in line and '；' not in line and '。' not in line:
                current_section.title = current_section.title + line
                current_section_title_row = 2 # 第2行标题
            else:
                current_section.text.append(line)
                current_section_title_row = 0
        else:
            print(f'Exception in page{page_num}:{line}')


# 转换为 JSON 格式
tree_dict = node_to_dict(root)
tree_json = json.dumps(tree_dict, ensure_ascii=False, indent=4)

for pre, fill, node in RenderTree(root):
    if node.depth <=2:
        print(f"{pre}{node.name}{node.title}")

print(tree_json)

with open('R7.json', 'w') as file:
    file.write(tree_json)

Exception in page15:大型飞机公共航空运输承运人
Exception in page15:运行合格审定规则
CCAR-121-R7大型飞机公共航空运输承运人运行合格审定规则
├── A总则
│   ├── 121.1目的和依据
│   ├── 121.3适用范围
│   ├── 121.5定义
│   ├── 121.7运行合格审定和持续监督
│   ├── 121.9飞机的湿租
│   └── 121.11境外运行规则
├── B运行合格审定的一般规定
│   ├── 121.20运行合格证及其运行规范
│   ├── 121.21运行合格证及其运行规范的申请和颁发程序
│   ├── 121.23运行合格证及其运行规范的颁发条件
│   ├── 121.25运行合格证及其运行规范的内容
│   ├── 121.27运行合格证及其运行规范的有效性
│   ├── 121.29运行合格证及其运行规范的检查
│   ├── 121.31运行合格证的修改
│   ├── 121.33合格证持有人保存和使用运行规范的责任
│   ├── 121.35运行规范的修改
│   └── 121.37申请人的责任
├── C管理运行合格证持有人的一般规定
│   ├── 121.41监察和检查的实施
│   ├── 121.42安全管理体系
│   ├── 121.43按照本规则实施运行所必需的管理人员和机构
│   ├── 121.45管理人员的合格条件
│   ├── 121.47运行的近期经历
│   ├── 121.49主运营基地、飞行基地和维修基地
│   ├── 121.51合格证持有人名称的使用
│   ├── 121.53按照军方合同实施运行的偏离批准
│   ├── 121.55实施应急运行的偏离批准
│   └── 121.57遵守运行合格证及其运行规范的要求
├── E国内、国际定期载客运行航路的批准
│   ├── 121.91航路批准的基本要求
│   ├── 121.93航路宽度
│   ├── 121.95必需的机场资料
│   ├── 121.97通信设施
│   ├── 121.99气象服务
│   ├── 121.101航路导航设施
│   ├── 121.103飞行签派中心
│   └── 121.105地面服务
├── F

In [2]:
import fitz
import re
from anytree import Node, RenderTree
import json

# Open the PDF file
pdf_path = "source_pdf/CCAR-121R8《大型飞机公共航空运输承运人运行合格审定规则》.pdf"
doc = fitz.open(pdf_path)

# 构建结构树
root = Node('CCAR-121-R8')
root.title = "大型飞机公共航空运输承运人运行合格审定规则"

# Skip the first 3 pages
start_page = 4
end_page = 289

sections = {}
current_chapter = None  # 章 A章
current_section = None  # 条 第 121.21 条
current_unit = None     # 单元, (a)
current_item = None     # 项，(1)
current_roman = None    # 罗马数字，(i)

# 记录当前节 标题行号
current_section_title_row = 0

chapter_patterns = [re.compile(r'^\s*([A-Z]) 章 (.*)'), re.compile(r'([A-Z])章 (.*)')]
section_patterns = [re.compile(r'^\s*第\s*(\d+\.\d+)\s*条 \s*(.*)')]
unit_patterns = [re.compile(r'^\s*[（(]([a-z])[）)](.*)')]
item_patterns = [re.compile(r'^\s*[（(](\d+)[）)](.*)')]
roman_patterns = [re.compile(r'^\s*[（(]([ivx]+)[）)](.*)')]
header_footer_patterns = [re.compile(r'^\s*(大型飞机公共航空运输承运人运行合格审定规则|-\d+-)\s*$')]

def match_pattern(line, patterns):
    matched = False
    pattern_matched = None
    for reg in patterns:
        pattern_matched = reg.match(line)
        if pattern_matched:
            matched = True
            break
    return matched, pattern_matched

# Function to clean headers and footers
def clean_header_footer(page_text):
    clean_lines = []
    for line in page_text.split('\n'):
        matched = False
        for reg in header_footer_patterns:
            if reg.match(line):
                matched = True
                break
        if not matched:
            clean_lines.append(line)
    return "\n".join(clean_lines)

# 函数来检查是否有加粗属性
def is_bold(span):
    font_flags = span['flags']
    # font_flags 的 1 位表示 bold
    return font_flags & 1 == 1

# 识别一页里是否有加粗的行，并且返回加粗的行
def bold_lines_in_page(page_blocks):
    bold_lines = []
    for block in page_blocks:
        if block["type"] != 0:  # 仅处理文本块
            continue
        for line in block["lines"]:
            line_text = ""
            for span in line["spans"]:
                print(span)
                if is_bold(span):
                    bold_lines.append(span["text"])
    return bold_lines

# 函数将树形结构转换为字典，并包含自定义字段
def node_to_dict(node):
    return {
        "name": node.name,
        "title": getattr(node, "title", ""),
        "text": getattr(node, "text", ""),
        "children": [node_to_dict(child) for child in node.children]
    }

# 获取当前节点的前一个同级节点
def get_previous_sibling(node):
    siblings = node.parent.children
    index = siblings.index(node)
    if index > 0:
        return siblings[index - 1]
    return None

from anytree import Node, RenderTree

# 获取parent节点的children中index最大的节点
def get_last_node(parent_node):
    siblings = parent_node.children
    return siblings[-1] if siblings else None


# Iterate through the pages and extract text
for page_num in range(start_page - 1, end_page):
# for page_num in range(194, 195):
    page = doc.load_page(page_num)
    page_text = page.get_text("text")
    blocks = page.get_text("dict")["blocks"]
    cleaned_page_text = clean_header_footer(page_text)
    
    for line in cleaned_page_text.split('\n'):
        line = line.strip()
        if line == '':
            continue
        # print(line)

        # 修复 第 121.713 附加要求 这条数据
        if line == '第 121.713 附加要求':
            line = '第 121.713 条 附加要求'
        
        # 匹配新章，eg：B运行合格审定的一般规定
        chapter_matched, chapter_matches = match_pattern(line, chapter_patterns)
        if chapter_matched:
            chapter_num = chapter_matches.group(1).strip()
            chapter_title = chapter_matches.group(2).strip()
            current_chapter = Node(chapter_num, parent = root, title = chapter_title, text = [])

            # 开始新的章，重置子节点
            current_section = None
            current_unit = None
            current_item = None
            current_roman = None

            # 跳过后续处理，进入下一行循环
            continue

        # 匹配新条款， eg：第121.31条
        section_matched, section_matches = match_pattern(line, section_patterns)
        if section_matched and current_chapter != None:
            section_num = section_matches.group(1).strip()
            section_title = section_matches.group(2).strip()

            section_num1 = int(section_num.split('.')[0])
            section_num2 = int(section_num.split('.')[1])
            current_section_num2 = int(current_section.name.split('.')[1]) if current_section is not None else None
            # if section_num1 == 121 and section_num2 == 367:
            #     print(f"==============>{section_num1}, {section_num2}, {current_section_num2}")
            # 判断是否为被正确提取的条
            if current_section is None \
                or (',' not in section_title and '，' not in section_title and ';' not in section_title and '；' not in section_title and '。' not in section_title and \
                    section_num1 == 121 and section_num2 > current_section_num2  and section_num2 - current_section_num2 <= 100 ):
                current_section = Node(section_num, parent = current_chapter, title = section_title, text = [])
                # 节 标题行号重置为1
                current_section_title_row = 1
    
                # 开始新的条，重置子节点
                current_unit = None
                current_item = None
                current_roman = None
    
                # 跳过后续处理，进入下一行循环
                continue
        
        # 匹配新单元，eg：(a)
        unit_matched, unit_matches = match_pattern(line, unit_patterns)
        if unit_matched and current_section != None:
            unit_num = unit_matches.group(1).strip()
            unit_text = unit_matches.group(2).strip()
            # 需要区分 unit 里的 (i) 和罗马数字的 (i)，主要看当前的编号和前面的编号是否相连
            # 这里有bug，unit为h，后续(1/2...), 其中包含(i)会解析出错
            if unit_num == 'a' or (current_unit != None and (ord(unit_num) - ord(current_unit.name) == 1)):
                current_unit = Node(unit_num, parent = current_section, text = [unit_text])
            
                # 开始新的单元，重置子节点
                current_item = None
                current_roman = None

                # 跳过后续处理，进入下一行循环
                continue

        # 匹配新项，eg：(1)
        item_matched, item_matches = match_pattern(line, item_patterns)
        if item_matched and current_unit != None:
            item_num = item_matches.group(1).strip()
            item_text = item_matches.group(2).strip()
            current_item = Node(item_num, parent = current_unit, text = [item_text])
            
            # 开始新的单元，重置子节点
            current_roman = None

            # 跳过后续处理，进入下一行循环
            continue
        
        # 匹配罗马数字，eg：(i)
        roman_matched, roman_matches = match_pattern(line, roman_patterns)
        if roman_matched and current_item != None:
            roman_num = roman_matches.group(1).strip()
            roman_text = roman_matches.group(2).strip()
            current_roman = Node(roman_num, parent = current_item, text = [roman_text])

            # 跳过后续处理，进入下一行循环
            continue

        # print(current_item.name if current_item else 'xxx')
        # 本行无匹配
        if current_roman != None:
            current_roman.text.append(line)
        elif current_item != None:
            current_item.text.append(line)
        elif current_unit != None:
            current_unit.text.append(line)
        elif current_section != None:
            # 判断是否为第二行标题内容 还是 正文内容 (假设最多只有两行标题)
            if current_section_title_row == 1 and len(line) <= 20 and ',' not in line and '，' not in line and ';' not in line and '；' not in line and '。' not in line:
                current_section.title = current_section.title + line
                current_section_title_row = 2 # 第2行标题
            else:
                current_section.text.append(line)
                current_section_title_row = 0
        else:
            print(f'Exception in page{page_num}:{line}')


# 转换为 JSON 格式
tree_dict = node_to_dict(root)
tree_json = json.dumps(tree_dict, ensure_ascii=False, indent=4)

for pre, fill, node in RenderTree(root):
    if node.depth <=2:
        print(f"{pre}{node.name}{node.title}")

print(tree_json)

with open('R8.json', 'w') as file:
    file.write(tree_json)

CCAR-121-R8大型飞机公共航空运输承运人运行合格审定规则
├── A总   则
│   ├── 121.1目的和依据
│   ├── 121.3适用范围
│   ├── 121.5定义
│   ├── 121.7运行合格审定和持续监督
│   ├── 121.9飞机的湿租
│   └── 121.11境外运行规则
├── B运行合格审定的一般规定
│   ├── 121.20运行合格证及其运行规范
│   ├── 121.21运行合格证及其运行规范的申请和颁发程序
│   ├── 121.23运行合格证及其运行规范的颁发条件
│   ├── 121.25运行合格证及其运行规范的内容
│   ├── 121.27运行合格证及其运行规范的有效性
│   ├── 121.29运行合格证及其运行规范的检查
│   ├── 121.31运行合格证的修改
│   ├── 121.33合格证持有人保存和使用运行规范的责任
│   ├── 121.35运行规范的修改
│   └── 121.37申请人的责任
├── C管理合格证持有人的一般规定
│   ├── 121.41监察和检查的实施
│   ├── 121.42安全管理体系
│   ├── 121.43按照本规则实施运行所必需的管理人员和机构
│   ├── 121.45管理人员的合格条件
│   ├── 121.47运行的近期经历
│   ├── 121.49主运行基地、飞行基地和维修基地
│   ├── 121.51合格证持有人名称的使用
│   ├── 121.52飞行数据的使用
│   ├── 121.53按照军方合同实施运行的偏离批准
│   ├── 121.55实施应急运行的偏离批准
│   └── 121.57遵守运行合格证及其运行规范的要求
├── E国内、国际定期载客运行航路的批准
│   ├── 121.91航路批准的基本要求
│   ├── 121.93航路宽度
│   ├── 121.95必需的机场资料
│   ├── 121.97通信设备
│   ├── 121.99气象服务
│   ├── 121.101航路导航设施
│   ├── 121.103运行控制中心
│   └── 121.105地面服务
├── F补充运行的区域和航路批准
│   ├── 121.113航路和区域要求概则
│ 

In [3]:
import json

with open('R7.json', 'r') as file:
    r7_json = json.load(file)
    
with open('R8.json', 'r') as file:
    r8_json = json.load(file)

In [4]:
r7_json

{'name': 'CCAR-121-R7',
 'title': '大型飞机公共航空运输承运人运行合格审定规则',
 'text': '',
 'children': [{'name': 'A',
   'title': '总则',
   'text': [],
   'children': [{'name': '121.1',
     'title': '目的和依据',
     'text': ['为了对大型飞机公共航空运输承运人进行运行合格审定和持续监督检查，',
      '保证其达到并保持规定的运行安全水平，根据《中华人民共和国民用航空法》',
      '和《国务院对确需保留的行政审批项目设定行政许可的决定》制定本规则。'],
     'children': []},
    {'name': '121.3',
     'title': '适用范围',
     'text': [],
     'children': [{'name': 'a',
       'title': '',
       'text': ['本规则适用于在中华人民共和国境内依法设立的航空运营人实施的下', '列公共航空运输运行：'],
       'children': [{'name': '1',
         'title': '',
         'text': ['使用最大起飞全重超过 5,700 千克的多发飞机实施的定期载客运输飞', '行；'],
         'children': []},
        {'name': '2',
         'title': '',
         'text': ['使用旅客座位数超过 30 座或者最大商载超过 3,400 千克的多发飞机实', '施的不定期载客运输飞行；'],
         'children': []},
        {'name': '3',
         'title': '',
         'text': ['使用最大商载超过 3,400 千克的多发飞机实施的全货物运输飞行。'],
         'children': []}]},
      {'name': 'b',
       'title': '',
       'text'

In [5]:
r8_json

{'name': 'CCAR-121-R8',
 'title': '大型飞机公共航空运输承运人运行合格审定规则',
 'text': '',
 'children': [{'name': 'A',
   'title': '总   则',
   'text': [],
   'children': [{'name': '121.1',
     'title': '目的和依据',
     'text': ['为了对大型飞机公共航空运输承运人进行运行合格审',
      '定和持续监督检查，保证其达到并保持规定的运行安全水',
      '平，根据《中华人民共和国民用航空法》和《国务院对确需',
      '保留的行政审批项目设定行政许可的决定》，制定本规则。'],
     'children': []},
    {'name': '121.3',
     'title': '适用范围',
     'text': [],
     'children': [{'name': 'a',
       'title': '',
       'text': ['本规则适用于在中华人民共和国境内依法设立的航', '空运营人实施的下列公共航空运输运行：'],
       'children': [{'name': '1',
         'title': '',
         'text': ['使用最大起飞重量超过 5,700 千克的多发涡轮驱动飞', '机实施的定期载客运输飞行；'],
         'children': []},
        {'name': '2',
         'title': '',
         'text': ['使用旅客座位数超过 30 座或者最大商载超过 3,400', '千克的多发涡轮驱动飞机实施的不定期载客运输飞行；'],
         'children': []},
        {'name': '3',
         'title': '',
         'text': ['使用最大商载超过 3,400 千克的多发涡轮驱动飞机实', '施的全货物运输飞行。'],
         'children': []}]},
      {'name': 'b',
    

In [8]:
# r7_json['children'][0-25] # A章 chapter
# r7_json['children'][1]['children'][8] # 第 xxx 条 section
# r7_json['children'][1]['children'][8]['children'][1] # (b) unit
# r7_json['children'][1]['children'][8]['children'][1]['children'][2] # (3) item
# r7_json['children'][1]['children'][8]['children'][1]['children'][2]['children'][0] # (i) roman

In [6]:
# 获取所有 '条的编号' 列表
r7_section_list = [section['name'] for chapter in r7_json['children'] for section in chapter['children']]
r8_section_list = [section['name'] for chapter in r8_json['children'] for section in chapter['children']]

In [7]:
print(len(r7_section_list))
print(len(r8_section_list))

302
302


In [8]:
# 差异部分的 '条'
different_section_8_vs_7 = sorted(list(set(r8_section_list) - set(r7_section_list)), key=lambda x:int(x.split('.')[1]))

different_section_7_vs_8 = sorted(list(set(r7_section_list) - set(r8_section_list)), key=lambda x:int(x.split('.')[1]))

In [11]:
# 相同ID的 '条', 需要进一步比较
to_compare_section = [section for section in r8_section_list if section not in different_section_8_vs_7]

In [13]:
# 遍历下级 合并所有text（针对unit，item）
def merge_text(input_json):
    res = "".join(input_json['text']).replace("\n", "")#顶层
    #合并第一层
    for child_lv1 in input_json['children']:
        child_lv1_text = "".join(child_lv1['text']).replace("\n", "")
        res = res + child_lv1_text
        #合并第二层
        for child_lv2 in child_lv1['children']:
            child_lv2_text = "".join(child_lv2['text']).replace("\n", "")
            res = res + child_lv2_text
    return res

In [14]:
# 数据初始化，生成 section, unit, item, roman 各个级别的 id:(level, title, text) 字典
# lv: section, unit, item, roman
# id: 【doc r7】_【chapter A】_【section 121.1】_【unit a】_【item 1】_【roman ii】 
# text 需要merge 所有下级 text:
#    1. 对与 section 来说，可能只有title，text 不需要进一步合并下级text，因为比较的时候只比较 title 和 section头部text
#    2. 对于 unit、item 来说，text需要按顺序，递归、拼接合并下级text
#    3. 对于 roman 来说，text只需要保持本来的内容即可

init_dict = {}

src_json_data = [('r7', r7_json), ('r8', r8_json)]

for doc in src_json_data:
    doc_name = doc[0]
    doc_data = doc[1]
    for chapter in doc_data['children']:
        chapter_name = chapter['name']
        chapter_title = chapter['title']
        # print(chapter_name, chapter_title)
        for section in chapter['children']:
            section_name = section['name']
            section_title = section['title']
            section_text = "".join(section['text']).replace("\n", "")
            # print(section_name, section_title)
            # print(section_text)
            section_key = f"{doc_name}_{chapter_name}_{section_name}"
            section_level = "section"
            init_dict[section_key] = (section_level, section_title, section_text)
            for unit in section['children']:
                unit_name = unit['name']
                unit_title = unit['title']
                unit_text = merge_text(unit)
                # print(unit_name, unit_title)
                # print(unit_text)
                unit_key = f"{doc_name}_{chapter_name}_{section_name}_{unit_name}"
                unit_level = "unit"
                init_dict[unit_key] = (unit_level, unit_title, unit_text)
                for item in unit['children']:
                    item_name = item['name']
                    item_title = item['title']
                    item_text = merge_text(item)
                    # print(item_name, item_title)
                    # print(item_text)
                    item_key = f"{doc_name}_{chapter_name}_{section_name}_{unit_name}_{item_name}"
                    item_level = "item"
                    init_dict[item_key] = (item_level, item_title, item_text)
                    for roman in item['children']:
                        roman_name = roman['name']
                        roman_title = roman['title']
                        roman_text = merge_text(roman)
                        # print(roman_name, roman_title)
                        # print(roman_text)
                        roman_key = f"{doc_name}_{chapter_name}_{section_name}_{unit_name}_{item_name}_{roman_name}"
                        roman_level = "roman"
                        init_dict[roman_key] = (roman_level, roman_title, roman_text)


In [15]:
len(init_dict)

5302

In [16]:
import pickle
def read_dict_file(file_path):
    with open(file_path, 'rb') as f:
            data = pickle.load(f)
    return data

def save_dict_to_file(dict, file_path):
    with open(file_path, 'wb') as pickle_file:
        pickle.dump(dict, pickle_file)


In [17]:
# 保存字典文件
init_compare_data_file = 'init_r7_r8_compare_data.pkl'
save_dict_to_file(init_dict, init_compare_data_file)

In [18]:
# 读取 初始化字典文件
init_compare_data_file = 'init_r7_r8_compare_data.pkl'
init_compare_data = read_dict_file(init_compare_data_file)

In [19]:
len(init_compare_data)

5302

In [20]:
init_compare_data

{'r7_A_121.1': ('section',
  '目的和依据',
  '为了对大型飞机公共航空运输承运人进行运行合格审定和持续监督检查，保证其达到并保持规定的运行安全水平，根据《中华人民共和国民用航空法》和《国务院对确需保留的行政审批项目设定行政许可的决定》制定本规则。'),
 'r7_A_121.3': ('section', '适用范围', ''),
 'r7_A_121.3_a': ('unit',
  '',
  '本规则适用于在中华人民共和国境内依法设立的航空运营人实施的下列公共航空运输运行：使用最大起飞全重超过 5,700 千克的多发飞机实施的定期载客运输飞行；使用旅客座位数超过 30 座或者最大商载超过 3,400 千克的多发飞机实施的不定期载客运输飞行；使用最大商载超过 3,400 千克的多发飞机实施的全货物运输飞行。'),
 'r7_A_121.3_a_1': ('item', '', '使用最大起飞全重超过 5,700 千克的多发飞机实施的定期载客运输飞行；'),
 'r7_A_121.3_a_2': ('item',
  '',
  '使用旅客座位数超过 30 座或者最大商载超过 3,400 千克的多发飞机实施的不定期载客运输飞行；'),
 'r7_A_121.3_a_3': ('item', '', '使用最大商载超过 3,400 千克的多发飞机实施的全货物运输飞行。'),
 'r7_A_121.3_b': ('unit', '', '对于适用于本条(a)款规定的航空运营人，在本规则中称之为大型飞机公共航空运输承运人。'),
 'r7_A_121.3_c': ('unit',
  '',
  '对于应按照本规则审定合格的大型飞机公共航空运输承运人，中国民用航空局（以下简称民航局）及民航地区管理局按照审定情况在其运行合格证及其运行规范中批准其实施下列一项或者多项运行种类的运行：国内定期载客运行，是指符合本条(a)款第(1)项规定，在中华人民共和国境内两点之间的运行，或者一个国内地点与另一个由局方专门指定、视为国内地点的国外地点之间的运行；国际定期载客运行，是指符合本条(a)款第(1)项规定，在一个国内地点和一个国外地点之间，两个国外地点之间，或者一个国内地点与另一个由局方专门指定、视为国外地点的国内地点之间的运行；补充运行，是指符合本

In [21]:
from zhipuai import ZhipuAI

# 智谱AI Embedding长度设置为最大4096个汉字
def get_text_embedding_from_zhipu_api(input_str, max_text_length = 4096):
    if len(input_str) > max_text_length:
        print(f"超长文本embedding，即将被截断为4096长度: {input_str}")
    input_text = input_str.strip().replace("\n", "")[:max_text_length]
    client = ZhipuAI(api_key="1b2d462c253146a98518bbfc0ba1b9cc.4UwLIcOT0PW0v43r") 
    response = client.embeddings.create(
        model="embedding-2", 
        input=input_text,
    )
    return response.data[0].embedding


In [22]:
# 初始化 embedding, 生成新的字典文件 key:(level, title, text, text_embedding)
init_embd_data = {}

for key in init_compare_data:
    text = init_compare_data[key][2].strip()
    if text == '':
        text_embd = []
    else:
        text_embd = get_text_embedding_from_zhipu_api(text, max_text_length = 4096)
    init_embd_data[key] = (init_compare_data[key][0], init_compare_data[key][1], text, text_embd)

# 保存embd字典文件
init_embd_file = 'init_r7_r8_embd_data.pkl'
save_dict_to_file(init_embd_data, init_embd_file)

In [23]:
# 读取初始化数据
init_embd_file = 'init_r7_r8_embd_data.pkl'
src_data = read_dict_file(init_embd_file) # key:(level, title, text, text_embedding)
print(len(src_data))

5302


In [24]:
src_data['r7_A_121.3']

('section', '适用范围', '', [])

In [25]:
src_data['r7_A_121.1']

('section',
 '目的和依据',
 '为了对大型飞机公共航空运输承运人进行运行合格审定和持续监督检查，保证其达到并保持规定的运行安全水平，根据《中华人民共和国民用航空法》和《国务院对确需保留的行政审批项目设定行政许可的决定》制定本规则。',
 [0.009807973,
  0.03168431,
  -0.020186454,
  0.030626468,
  0.0143119525,
  -0.009409295,
  0.023893401,
  0.0141903255,
  -0.014972011,
  0.019349715,
  -0.0035566299,
  0.017759243,
  0.018085303,
  -0.003012071,
  -0.044936493,
  -0.048497174,
  0.004065726,
  0.014150117,
  0.0028388395,
  -0.018095639,
  0.0043934416,
  -0.01988498,
  0.048192002,
  -0.010170541,
  -0.064553365,
  -0.04333984,
  -0.0046788375,
  0.028653203,
  -0.015077773,
  -0.042696744,
  -0.0077582654,
  0.012018166,
  -0.045006655,
  0.01308903,
  0.0103076305,
  0.011439305,
  -0.04182514,
  0.028294107,
  0.033054776,
  -0.046008006,
  -0.0056522656,
  0.0047694603,
  -0.010505224,
  -0.0072882692,
  0.0093854405,
  0.04189858,
  0.028302465,
  0.026674872,
  -0.04209075,
  0.059694584,
  -0.010745325,
  0.016879536,
  -0.043708652,
  -0.031378146,
  0.008718766,
  -0.0046340767,
 

In [27]:
# 获取所有 '条的编号' 列表
r7_section_list = sorted([key.split('_')[-1] for key in src_data if key.startswith('r7_') and src_data[key][0] == 'section'], key=lambda x: int(x.split('.')[1]))
r8_section_list = sorted([key.split('_')[-1] for key in src_data if key.startswith('r8_') and src_data[key][0] == 'section'], key=lambda x: int(x.split('.')[1]))

print(len(r7_section_list), r7_section_list[0])
print(len(r8_section_list), r8_section_list[0])

302 121.1
302 121.1


In [28]:
# R8 多出来的的 '条'
different_section_8_vs_7 = sorted(list(set(r8_section_list) - set(r7_section_list)), key=lambda x:int(x.split('.')[1]))
print(len(different_section_8_vs_7))
different_section_8_vs_7

12


['121.52',
 '121.441',
 '121.519',
 '121.526',
 '121.530',
 '121.554',
 '121.610',
 '121.611',
 '121.702',
 '121.704',
 '121.706',
 '121.760']

In [29]:
# R7 多出来的的 '条'
different_section_7_vs_8 = sorted(list(set(r7_section_list) - set(r8_section_list)), key=lambda x:int(x.split('.')[1]))
print(len(different_section_7_vs_8))
different_section_7_vs_8

12


['121.175',
 '121.177',
 '121.179',
 '121.181',
 '121.183',
 '121.185',
 '121.187',
 '121.327',
 '121.331',
 '121.343',
 '121.708',
 '121.727']

In [30]:
# 相同ID的 '条', 需要进一步比较
to_compare_section = [section for section in r8_section_list if section not in different_section_8_vs_7]
print(len(to_compare_section))
to_compare_section

290


['121.1',
 '121.3',
 '121.5',
 '121.7',
 '121.9',
 '121.11',
 '121.20',
 '121.21',
 '121.23',
 '121.25',
 '121.27',
 '121.29',
 '121.31',
 '121.33',
 '121.35',
 '121.37',
 '121.41',
 '121.42',
 '121.43',
 '121.45',
 '121.47',
 '121.49',
 '121.51',
 '121.53',
 '121.55',
 '121.57',
 '121.91',
 '121.93',
 '121.95',
 '121.97',
 '121.99',
 '121.101',
 '121.103',
 '121.105',
 '121.113',
 '121.115',
 '121.117',
 '121.119',
 '121.121',
 '121.123',
 '121.125',
 '121.127',
 '121.131',
 '121.133',
 '121.135',
 '121.137',
 '121.151',
 '121.153',
 '121.155',
 '121.157',
 '121.159',
 '121.161',
 '121.171',
 '121.173',
 '121.189',
 '121.191',
 '121.193',
 '121.195',
 '121.197',
 '121.211',
 '121.213',
 '121.215',
 '121.217',
 '121.301',
 '121.305',
 '121.307',
 '121.308',
 '121.309',
 '121.310',
 '121.311',
 '121.312',
 '121.313',
 '121.314',
 '121.315',
 '121.316',
 '121.317',
 '121.318',
 '121.319',
 '121.320',
 '121.323',
 '121.325',
 '121.329',
 '121.333',
 '121.335',
 '121.337',
 '121.339',
 '12

In [31]:
# 对于相同‘条’的部分， 生成 section_number : (r37_dict_key, r38_dict_key)的映射
section_num_map_dict_key_r7 = {}
section_num_map_dict_key_r8 = {}

for key in src_data:
    if src_data[key][0] == 'section':
        doc = key.split('_')[0]
        chapter = key.split('_')[1]
        section = key.split('_')[2]
        if section in to_compare_section:
            if doc == 'r7':
                section_num_map_dict_key_r7[section] = key
            else:
                section_num_map_dict_key_r8[section] = key
    

In [32]:
# 先看一下 section（条） 标题 和 头部正文对比的情况

# section（条）标题不同的部分
different_section_title = {}

for section_id in to_compare_section:
    r7_section_key = section_num_map_dict_key_r7[section_id]
    r8_section_key = section_num_map_dict_key_r8[section_id]
    # print(r7_section_key, r8_section_key)
    
    r7_section_title = src_data[r7_section_key][1]
    r8_section_title = src_data[r8_section_key][1]
    # 打印title不同的部分
    if r7_section_title != r8_section_title:
        different_section_title[section_id] = (r7_section_title, r8_section_title)
        print(r7_section_title)
        print(r8_section_title)
        print()

主运营基地、飞行基地和维修基地
主运行基地、飞行基地和维修基地

通信设施
通信设备

飞行签派中心
运行控制中心

总则
概则

涡轮发动机飞机用于生命保障的补充供氧要求
涡轮发动机飞机用于生命保障的补充氧气要求

快速存取记录器或等效设备
快速存取记录器或者等效设备

地形提示和警告系统
地形感知和警告系统(TAWS)

驾驶舱话音记录器
飞行记录器

近地警告／下滑道偏离警告系统
其他安全措施与遇险要求

总则
概则

维修系统的机构和人员
维修工程管理部门的机构和人员

培训大纲和人员技术档案
培训政策和人员技术档案

机组成员的安保训练
安保训练

高级训练大纲的一般要求
基于胜任力的培训和评估方案的一般要求

高级训练大纲的批准
基于胜任力的培训和评估方案的批准

执照或等级颁发的条件
执照或者等级颁发的条件

由他人提供训练、资格认定或检查安排的批准
由他人提供训练、资格认定或者检查安排的批准

基于性能的导航运行（PBN）
基于性能的导航运行(PBN)

广播式自动相关监视（ADS-B）
广播式自动相关监视(ADS-B)

管制员-飞行员数据链通信（CPDLC）
管制员-飞行员数据链通信(CPDLC)

平视显示器（HUD）或等效显示器、 增强视景系统（EVS）、
平视显示器(HUD)或者等效显示器、增强

电子飞行包（EFB）
电子飞行包(EFB)

客舱和驾驶舱内大件物品的固定
客舱和驾驶舱内行李和物品的固定

使用困难报告（运行）
使用困难报告

总则
概则

备降和改航机场的附加要求
附加要求

通信设施的附加要求
延程运行(EDTO)的通信设备

延程运行备降机场：救援与消防服务
延程运行(EDTO)备降机场：救援与消防服务



In [33]:
# 63 个 '条' 标题不同
print(len(different_section_title))
different_section_title

28


{'121.49': ('主运营基地、飞行基地和维修基地', '主运行基地、飞行基地和维修基地'),
 '121.97': ('通信设施', '通信设备'),
 '121.103': ('飞行签派中心', '运行控制中心'),
 '121.211': ('总则', '概则'),
 '121.329': ('涡轮发动机飞机用于生命保障的补充供氧要求', '涡轮发动机飞机用于生命保障的补充氧气要求'),
 '121.352': ('快速存取记录器或等效设备', '快速存取记录器或者等效设备'),
 '121.354': ('地形提示和警告系统', '地形感知和警告系统(TAWS)'),
 '121.359': ('驾驶舱话音记录器', '飞行记录器'),
 '121.360': ('近地警告／下滑道偏离警告系统', '其他安全措施与遇险要求'),
 '121.362': ('总则', '概则'),
 '121.371': ('维修系统的机构和人员', '维修工程管理部门的机构和人员'),
 '121.372': ('培训大纲和人员技术档案', '培训政策和人员技术档案'),
 '121.422': ('机组成员的安保训练', '安保训练'),
 '121.505': ('高级训练大纲的一般要求', '基于胜任力的培训和评估方案的一般要求'),
 '121.508': ('高级训练大纲的批准', '基于胜任力的培训和评估方案的批准'),
 '121.513': ('执照或等级颁发的条件', '执照或者等级颁发的条件'),
 '121.515': ('由他人提供训练、资格认定或检查安排的批准', '由他人提供训练、资格认定或者检查安排的批准'),
 '121.521': ('基于性能的导航运行（PBN）', '基于性能的导航运行(PBN)'),
 '121.523': ('广播式自动相关监视（ADS-B）', '广播式自动相关监视(ADS-B)'),
 '121.525': ('管制员-飞行员数据链通信（CPDLC）', '管制员-飞行员数据链通信(CPDLC)'),
 '121.527': ('平视显示器（HUD）或等效显示器、 增强视景系统（EVS）、', '平视显示器(HUD)或者等效显示器、增强'),
 '121.529': ('电子飞行包（EFB）', '电子飞行

In [34]:
import numpy as np

def cal_similarity(embd1, embd2):
    score = 0
    if len(embd1) != 0 and len(embd2) != 0:
        score = np.dot(embd1, embd2) / (np.linalg.norm(embd1) * np.linalg.norm(embd2))
    return score

In [35]:
# 先看一下 section（条） 标题 和 头部正文对比的情况

# section（条）头部正文 不同的部分
different_section_text = {}

for section_id in to_compare_section:
    r7_section_key = section_num_map_dict_key_r7[section_id]
    r8_section_key = section_num_map_dict_key_r8[section_id]
    # print(r7_section_key, r8_section_key)
    
    r7_section_text = src_data[r7_section_key][2]
    r8_section_text = src_data[r8_section_key][2]
    r7_section_text_embd = src_data[r7_section_key][3]
    r8_section_text_embd = src_data[r8_section_key][3]
    
    # 头部正文 不同的部分
    if r7_section_text != r8_section_text:
        simi_score = cal_similarity(r7_section_text_embd, r8_section_text_embd)
        different_section_text[section_id] = (r7_section_text, r8_section_text, simi_score)
        # print(r7_section_text)
        # print(r8_section_text)
        # print()

In [36]:
# 85 个 '条' 头部正文 不同
print(len(different_section_text))
different_section_text

49


{'121.1': ('为了对大型飞机公共航空运输承运人进行运行合格审定和持续监督检查，保证其达到并保持规定的运行安全水平，根据《中华人民共和国民用航空法》和《国务院对确需保留的行政审批项目设定行政许可的决定》制定本规则。',
  '为了对大型飞机公共航空运输承运人进行运行合格审定和持续监督检查，保证其达到并保持规定的运行安全水平，根据《中华人民共和国民用航空法》和《国务院对确需保留的行政审批项目设定行政许可的决定》，制定本规则。',
  0.9990111212184923),
 '121.11': ('大型飞机公共航空运输承运人在中国境外运行时，应当遵守《国际民用航空公约》附件二《空中规则》和所适用的外国法规。在《民用航空器驾驶员合格审定规则》（CCAR61）、《一般运行和飞行规则》（CCAR91）和本规则的规定严于上述附件和外国法规的规定并且不与其发生抵触时，还应当遵守《民用航空器驾驶员合格审定规则》（CCAR61）、《一般运行和飞行规则》（CCAR91）和本规则的规定。',
  '大型飞机公共航空运输承运人在中国境外运行时，应当遵守《国际民用航空公约》附件 2《空中规则》和所适用的外国法规。在《民用航空器驾驶员合格审定规则》(CCAR-61)、《一般运行和飞行规则》(CCAR-91)和本规则的规定严于上述附件和外国法规的规定并且不与其发生抵触时，还应当遵守《民用航空器驾驶员合格审定规则》(CCAR-61)、《一般运行和飞行规则》(CCAR-91)和本规则的规定。',
  0.9936891281285929),
 '121.29': ('合格证持有人应当将其运行合格证及其运行规范保存在主运营基地，并能随时接受局方的检查，合格证持有人的飞机上应携带运行合格证及其运行规范复印件。',
  '合格证持有人应当将其运行合格证及其运行规范保存在主运行基地，并能随时接受局方的检查。合格证持有人的飞机上应当携带运行合格证及其运行规范经认证的真实副本，并保证副本与正本一致。该副本可以是纸质版，也可以是符合局方要求的其他形式。',
  0.9432303440553902),
 '121.37': ('申请人申请或者申请修改运行合格证及其运行规范以及与运行合格审定有关的其他项目，应当保证申请材料真实完整。',
  '申请人申请取得或者申请修改运行合格证及其运行规范以及与运行合

In [37]:
# 对于可以拆分到‘(a/b/c..)’的部分， 生成 section_number : [unit_key]的映射
unit_num_map_dict_key_r7 = {}
unit_num_map_dict_key_r8 = {}

for key in src_data:
    if src_data[key][0] == 'unit':
        doc = key.split('_')[0]
        chapter = key.split('_')[1]
        section = key.split('_')[2]
        unit = key.split('_')[3]
        if doc == 'r7':
            if section in unit_num_map_dict_key_r7:
                unit_num_map_dict_key_r7[section].append(key)
            else:
                unit_num_map_dict_key_r7[section] = [key]
        else:
            if section in unit_num_map_dict_key_r8:
                unit_num_map_dict_key_r8[section].append(key)
            else:
                unit_num_map_dict_key_r8[section] = [key]
    

In [38]:
print(len(unit_num_map_dict_key_r7))
print(len(unit_num_map_dict_key_r8))

243
242


In [39]:
unit_num_map_dict_key_r7

{'121.3': ['r7_A_121.3_a',
  'r7_A_121.3_b',
  'r7_A_121.3_c',
  'r7_A_121.3_d',
  'r7_A_121.3_e',
  'r7_A_121.3_f'],
 '121.5': ['r7_A_121.5_a', 'r7_A_121.5_b'],
 '121.7': ['r7_A_121.7_a',
  'r7_A_121.7_b',
  'r7_A_121.7_c',
  'r7_A_121.7_d',
  'r7_A_121.7_e'],
 '121.9': ['r7_A_121.9_a',
  'r7_A_121.9_b',
  'r7_A_121.9_c',
  'r7_A_121.9_d',
  'r7_A_121.9_e'],
 '121.20': ['r7_B_121.20_a', 'r7_B_121.20_b'],
 '121.21': ['r7_B_121.21_a',
  'r7_B_121.21_b',
  'r7_B_121.21_c',
  'r7_B_121.21_d',
  'r7_B_121.21_e',
  'r7_B_121.21_f'],
 '121.23': ['r7_B_121.23_a', 'r7_B_121.23_b'],
 '121.25': ['r7_B_121.25_a', 'r7_B_121.25_b'],
 '121.27': ['r7_B_121.27_a', 'r7_B_121.27_b', 'r7_B_121.27_c'],
 '121.31': ['r7_B_121.31_a', 'r7_B_121.31_b', 'r7_B_121.31_c'],
 '121.33': ['r7_B_121.33_a', 'r7_B_121.33_b', 'r7_B_121.33_c'],
 '121.35': ['r7_B_121.35_a',
  'r7_B_121.35_b',
  'r7_B_121.35_c',
  'r7_B_121.35_d',
  'r7_B_121.35_e'],
 '121.41': ['r7_C_121.41_a',
  'r7_C_121.41_b',
  'r7_C_121.41_c',
  'r7_C

In [40]:
# r7,r8都可以进一步分解到unit的部分，开始对比 unit (a/b/c..) 

# 首先获得所有相同的 unit部分
same_unit_list = {}

for section_id in to_compare_section:
    # 尝试取出同一 条 下面所有的a/b/c
    r7_unit_keys = unit_num_map_dict_key_r7[section_id] if section_id in unit_num_map_dict_key_r7 else []
    r8_unit_keys = unit_num_map_dict_key_r8[section_id] if section_id in unit_num_map_dict_key_r8 else []
    # print(r7_unit_keys)
    # print(r8_unit_keys)
    # print()

    # 确认都可以进一步分解到 a/b/c，才需要进一步对比
    if len(r7_unit_keys) > 0 and len(r8_unit_keys) > 0:
        # 尝试对比同一unit的内容是否完全相同
        # 尝试取出 相同a/b/c的 内容完全相同的 unit_key
        for r8_unit_key in r8_unit_keys:
            r8_unit_text = src_data[r8_unit_key][2].strip().replace("\n","")

            # 尝试先寻找相同编号 a/b/c 
            tmp_r7_unit_key = r8_unit_key.replace('r8', 'r7')
            if tmp_r7_unit_key in r7_unit_keys:
                r7_unit_text = src_data[tmp_r7_unit_key][2].strip().replace("\n","")
                if r8_unit_text == r7_unit_text:
                    # 找到相同文本
                    if section_id in same_unit_list:
                        same_unit_list[section_id].append((tmp_r7_unit_key, r8_unit_key))
                    else:
                        same_unit_list[section_id] = [(tmp_r7_unit_key, r8_unit_key)]
                    continue
                    
            # 如果相同编号 a/b/c 的内容不相同，需要进一步扫描整个 r7 相同节下所有 a/b/c
            for r7_unit_key in r7_unit_keys:
                r7_unit_text = src_data[r7_unit_key][2].strip().replace("\n","")
                if r8_unit_text == r7_unit_text:
                    # 找到相同文本
                    if section_id in same_unit_list:
                        same_unit_list[section_id].append((r7_unit_key, r8_unit_key))
                    else:
                        same_unit_list[section_id] = [(r7_unit_key, r8_unit_key)]
                    break
                    
    

In [41]:
same_unit_list

{'121.3': [('r7_A_121.3_b', 'r8_A_121.3_b'),
  ('r7_A_121.3_d', 'r8_A_121.3_d'),
  ('r7_A_121.3_e', 'r8_A_121.3_e'),
  ('r7_A_121.3_f', 'r8_A_121.3_f')],
 '121.5': [('r7_A_121.5_b', 'r8_A_121.5_b')],
 '121.9': [('r7_A_121.9_c', 'r8_A_121.9_c'), ('r7_A_121.9_e', 'r8_A_121.9_e')],
 '121.20': [('r7_B_121.20_a', 'r8_B_121.20_a')],
 '121.21': [('r7_B_121.21_b', 'r8_B_121.21_b'),
  ('r7_B_121.21_c', 'r8_B_121.21_c'),
  ('r7_B_121.21_f', 'r8_B_121.21_f')],
 '121.33': [('r7_B_121.33_c', 'r8_B_121.33_c')],
 '121.41': [('r7_C_121.41_a', 'r8_C_121.41_a'),
  ('r7_C_121.41_d', 'r8_C_121.41_d')],
 '121.42': [('r7_C_121.42_a', 'r8_C_121.42_a'),
  ('r7_C_121.42_d', 'r8_C_121.42_d')],
 '121.43': [('r7_C_121.43_c', 'r8_C_121.43_c'),
  ('r7_C_121.43_e', 'r8_C_121.43_e'),
  ('r7_C_121.43_f', 'r8_C_121.43_f'),
  ('r7_C_121.43_g', 'r8_C_121.43_g')],
 '121.47': [('r7_C_121.47_a', 'r8_C_121.47_a')],
 '121.51': [('r7_C_121.51_a', 'r8_C_121.51_a')],
 '121.53': [('r7_C_121.53_a', 'r8_C_121.53_a'),
  ('r7_C_121.5

In [42]:
# 计算两个列表内文本相似度，第一个列表M个文本，第二个列表N个文本
# 先计算 M * N 次 similarity
# 得分从高到低排序
# pair原则 不放回策略
# 一旦其中一个列表所有元素都获得了对应的相似对象，停止寻找
# 返回列表 [(key1_a, key1_b, simi_score)]
def cross_cal_similarity(data, key_list1, key_list2):
    tmp_res = []
    for key2 in key_list2:
        text2 = data[key2][2]
        embd2 = data[key2][3]
        for key1 in key_list1:
            text1 = data[key1][2]
            embd1 = data[key1][3]
            simi_score = cal_similarity(embd1, embd2)
            tmp_res.append((key1, key2, simi_score))
    # 排序交叉计算后的得分
    sorted_tmp_res = sorted(tmp_res, key=lambda x: x[2], reverse=True)
    # for info in sorted_tmp_res:
    #     print(info)
    
    # 尝试从得分高到低，不放回策略，取出配对，直至其中一个全部取完为止
    list1 = key_list1.copy()
    list2 = key_list2.copy()
    pair_res = []
    for tup in sorted_tmp_res:
        key1 = tup[0]
        key2 = tup[1]
        simi_score = tup[2]
        # 两个key都还没有被拿出，才认为配对
        if key1 in list1 and key2 in list2:
            pair_res.append((key1, key2, simi_score))
            # 拿出已配对key
            list1.remove(key1)
            list2.remove(key2)
        # 一旦其中一个全部被拿完，直接结束
        if len(list1) == 0 or len(list2) == 0:
            break
    return pair_res


In [43]:
[key for key in src_data if key.startswith('r7_C_121.45') and src_data[key][0] == 'unit']

['r7_C_121.45_a',
 'r7_C_121.45_b',
 'r7_C_121.45_c',
 'r7_C_121.45_d',
 'r7_C_121.45_e',
 'r7_C_121.45_f']

In [44]:
cross_cal_similarity(src_data, 
                     ['r7_C_121.45_a',
                         'r7_C_121.45_b',
                         'r7_C_121.45_c',
                         'r7_C_121.45_d',
                         'r7_C_121.45_e',
                         'r7_C_121.45_f'],
                     ['r8_C_121.45_a',
                         'r8_C_121.45_b',
                         'r8_C_121.45_c',
                         'r8_C_121.45_d',
                         'r8_C_121.45_e',
                         'r8_C_121.45_f',
                         'r8_C_121.45_g'])

[('r7_C_121.45_a', 'r8_C_121.45_b', 0.997741381113346),
 ('r7_C_121.45_c', 'r8_C_121.45_d', 0.9967930895996976),
 ('r7_C_121.45_b', 'r8_C_121.45_c', 0.9913293850550193),
 ('r7_C_121.45_f', 'r8_C_121.45_g', 0.9866754993142249),
 ('r7_C_121.45_d', 'r8_C_121.45_e', 0.9863431404903364),
 ('r7_C_121.45_e', 'r8_C_121.45_f', 0.9603739290381944)]

In [45]:
# 排除掉完全相同的unit , 同一节下 剩余的部分 尝试按照相似度比较

# simi_pair_unit_list = []

pair_unit_list = {}
r7_unpair_unit_list = {}
r8_unpair_unit_list = {}

for section_id in to_compare_section:
    # 尝试取出同一 条 下面所有的a/b/c
    r7_unit_keys = unit_num_map_dict_key_r7[section_id] if section_id in unit_num_map_dict_key_r7 else []
    r8_unit_keys = unit_num_map_dict_key_r8[section_id] if section_id in unit_num_map_dict_key_r8 else []

    # 一开始 全部记为对不上
    r7_unpair_unit_list[section_id] = r7_unit_keys.copy()
    r8_unpair_unit_list[section_id] = r8_unit_keys.copy()

    # 确认都可以进一步分解到 a/b/c，才需要进一步对比
    if len(r7_unit_keys) > 0 and len(r8_unit_keys) > 0:
        # 排除掉完全相同的 a/b/c
        if section_id in same_unit_list:
            r7_same_units = [tup[0] for tup in same_unit_list[section_id]]
            r8_same_units = [tup[1] for tup in same_unit_list[section_id]]
            r7_remain_units = [unit for unit in r7_unit_keys if unit not in r7_same_units]
            r8_remain_units = [unit for unit in r8_unit_keys if unit not in r8_same_units]
        else:
            r7_remain_units = r7_unit_keys.copy()
            r8_remain_units = r8_unit_keys.copy()
        # 剩余同一节下所有 不完全相同的 a/b/c 交叉计算相似度
        units_simi_res = cross_cal_similarity(src_data, r7_remain_units, r8_remain_units)
        
        # 先保存匹配结果，进一步手工确认阈值 (最终阈值 下限0.6, 上限0.8)
        # for pair_unit in units_simi_res:
        #     r7_unit_text = src_data[pair_unit[0]][2]
        #     r8_unit_text = src_data[pair_unit[1]][2]
        #     simi_pair_unit_list.append((pair_unit[0], pair_unit[1], pair_unit[2], r7_unit_text, r8_unit_text))

        r7_paired_unit = []
        r8_paired_unit = []
        for pair_unit in units_simi_res:
            r7_unit_key = pair_unit[0]
            r8_unit_key = pair_unit[1]
            unit_simi_score = pair_unit[2]
            r7_unit = r7_unit_key.split('_')[-2] + '_' + r7_unit_key.split('_')[-1]
            r8_unit = r8_unit_key.split('_')[-2] + '_' + r8_unit_key.split('_')[-1]
            
            # 保存 对上了的unit
            if unit_simi_score > 0.8 or (unit_simi_score >= 0.6 and unit_simi_score <= 0.8 and r7_unit == r8_unit):
                r7_paired_unit.append(r7_unit_key)
                r8_paired_unit.append(r8_unit_key)
                if section_id in pair_unit_list:
                    pair_unit_list[section_id].append((r7_unit_key, r8_unit_key, unit_simi_score))
                else:
                    pair_unit_list[section_id] = [(r7_unit_key, r8_unit_key, unit_simi_score)]

        # 各自所有 - 完全相同 - 对上了的 = 对不上的（不需要进一步拆分再比较）
        r7_unpaired_unit = [unit for unit in r7_remain_units if unit not in r7_paired_unit]
        r8_unpaired_unit = [unit for unit in r8_remain_units if unit not in r8_paired_unit]
        r7_unpair_unit_list[section_id] = r7_unpaired_unit.copy()
        r8_unpair_unit_list[section_id] = r8_unpaired_unit.copy()
        

In [23]:
# print(len(simi_pair_unit_list))

# # 先保存到本地excel
# import pandas as pd

# df = pd.DataFrame(simi_pair_unit_list, columns=['r7_unit_key', 'r8_unit_key', 'simi_score', 'r7_unit_text', 'r8_unit_text'])
# df.to_excel('unit_pair_result.xlsx', index=False)

In [46]:
pair_unit_list

{'121.3': [('r7_A_121.3_c', 'r8_A_121.3_c', 0.9974672763668931),
  ('r7_A_121.3_a', 'r8_A_121.3_a', 0.9681668131850695)],
 '121.5': [('r7_A_121.5_a', 'r8_A_121.5_a', 0.9867757176576308)],
 '121.7': [('r7_A_121.7_d', 'r8_A_121.7_d', 1.0),
  ('r7_A_121.7_c', 'r8_A_121.7_c', 0.9966037541841651),
  ('r7_A_121.7_e', 'r8_A_121.7_e', 0.9934265903130234),
  ('r7_A_121.7_b', 'r8_A_121.7_b', 0.9882870220712696),
  ('r7_A_121.7_a', 'r8_A_121.7_a', 0.9760512937234813)],
 '121.9': [('r7_A_121.9_d', 'r8_A_121.9_d', 0.9995188649106529),
  ('r7_A_121.9_b', 'r8_A_121.9_b', 0.9991775250455738),
  ('r7_A_121.9_a', 'r8_A_121.9_a', 0.9959797310133323)],
 '121.20': [('r7_B_121.20_b', 'r8_B_121.20_b', 0.9988435765745171)],
 '121.21': [('r7_B_121.21_a', 'r8_B_121.21_a', 0.9992007730453472),
  ('r7_B_121.21_e', 'r8_B_121.21_e', 0.9869970289476504),
  ('r7_B_121.21_d', 'r8_B_121.21_d', 0.9331548140382903)],
 '121.23': [('r7_B_121.23_b', 'r8_B_121.23_b', 0.995560072188032),
  ('r7_B_121.23_a', 'r8_B_121.23_a', 0

In [47]:
r7_unpair_unit_list

{'121.1': [],
 '121.3': [],
 '121.5': [],
 '121.7': [],
 '121.9': [],
 '121.11': [],
 '121.20': [],
 '121.21': [],
 '121.23': [],
 '121.25': [],
 '121.27': [],
 '121.29': [],
 '121.31': [],
 '121.33': [],
 '121.35': [],
 '121.37': [],
 '121.41': [],
 '121.42': [],
 '121.43': [],
 '121.45': [],
 '121.47': [],
 '121.49': [],
 '121.51': [],
 '121.53': [],
 '121.55': [],
 '121.57': [],
 '121.91': [],
 '121.93': [],
 '121.95': [],
 '121.97': [],
 '121.99': [],
 '121.101': [],
 '121.103': [],
 '121.105': [],
 '121.113': [],
 '121.115': [],
 '121.117': [],
 '121.119': [],
 '121.121': [],
 '121.123': [],
 '121.125': [],
 '121.127': [],
 '121.131': [],
 '121.133': [],
 '121.135': [],
 '121.137': [],
 '121.151': [],
 '121.153': [],
 '121.155': [],
 '121.157': [],
 '121.159': [],
 '121.161': [],
 '121.171': ['r7_I_121.171_b'],
 '121.173': ['r7_I_121.173_a', 'r7_I_121.173_d'],
 '121.189': [],
 '121.191': [],
 '121.193': [],
 '121.195': [],
 '121.197': [],
 '121.211': [],
 '121.213': [],
 '121.215'

In [48]:
r8_unpair_unit_list

{'121.1': [],
 '121.3': [],
 '121.5': [],
 '121.7': [],
 '121.9': [],
 '121.11': [],
 '121.20': [],
 '121.21': [],
 '121.23': [],
 '121.25': [],
 '121.27': [],
 '121.29': [],
 '121.31': [],
 '121.33': [],
 '121.35': [],
 '121.37': [],
 '121.41': [],
 '121.42': [],
 '121.43': [],
 '121.45': ['r8_C_121.45_a'],
 '121.47': [],
 '121.49': [],
 '121.51': [],
 '121.53': [],
 '121.55': [],
 '121.57': [],
 '121.91': [],
 '121.93': [],
 '121.95': [],
 '121.97': ['r8_E_121.97_a', 'r8_E_121.97_b', 'r8_E_121.97_c'],
 '121.99': [],
 '121.101': [],
 '121.103': ['r8_E_121.103_a', 'r8_E_121.103_b', 'r8_E_121.103_c'],
 '121.105': [],
 '121.113': [],
 '121.115': [],
 '121.117': [],
 '121.119': [],
 '121.121': [],
 '121.123': [],
 '121.125': [],
 '121.127': [],
 '121.131': [],
 '121.133': [],
 '121.135': [],
 '121.137': ['r8_G_121.137_d'],
 '121.151': [],
 '121.153': [],
 '121.155': [],
 '121.157': [],
 '121.159': [],
 '121.161': [],
 '121.171': ['r8_I_121.171_b', 'r8_I_121.171_c'],
 '121.173': [],
 '121.

In [49]:
# 对于对上了的 unit，继续拆分到下一级，再进行一轮比较

# 对于可以拆分到‘(1/2/3..)’的部分， 生成 unit : [items]的映射
r7_unit_map_item_keys = {}
r8_unit_map_item_keys = {}

for key in src_data:
    if src_data[key][0] == 'item':
        doc = key.split('_')[0]
        chapter = key.split('_')[1]
        section = key.split('_')[2]
        unit = key.split('_')[3]
        item = key.split('_')[4]
        unit_path = f'{doc}_{chapter}_{section}_{unit}'
        if doc == 'r7':
            if unit_path in r7_unit_map_item_keys:
                r7_unit_map_item_keys[unit_path].append(key)
            else:
                r7_unit_map_item_keys[unit_path] = [key]
        else:
            if unit_path in r8_unit_map_item_keys:
                r8_unit_map_item_keys[unit_path].append(key)
            else:
                r8_unit_map_item_keys[unit_path] = [key]
    
    

In [50]:
print(len(r7_unit_map_item_keys))
print(len(r8_unit_map_item_keys))

285
291


In [51]:
# 所有能对得上的 unit 继续比较
# 首先获得所有相同的 item 1/2/3 的部分
same_item_list = {} # r7_unit_key|r8_unit_key : [(r7_item_key, r8_item_key),...]

for section in pair_unit_list:
    pair_units_in_section = pair_unit_list[section]
    for unit_pair in pair_units_in_section:
        r7_unit_key = unit_pair[0]
        r8_unit_key = unit_pair[1]
        unit_pair_key = f'{r7_unit_key}|{r8_unit_key}' # 对得上的unit_pair 新的key
        # 尝试取出同一 unit 下面所有的 1/2/3
        r7_item_keys = r7_unit_map_item_keys[r7_unit_key] if r7_unit_key in r7_unit_map_item_keys else []
        r8_item_keys = r8_unit_map_item_keys[r8_unit_key] if r8_unit_key in r8_unit_map_item_keys else []
        # print(r7_item_keys)
        # print(r8_item_keys)
        # print()
    
        # 确认都可以进一步分解到 1/2/3，才需要进一步对比
        if len(r7_item_keys) > 0 and len(r8_item_keys) > 0:
            # 尝试对比同一item的内容是否完全相同
            # 尝试取出 相同1/2/3的 内容完全相同的 item_key
            for r8_item_key in r8_item_keys:
                r8_item_text = src_data[r8_item_key][2].strip().replace("\n","")
                # 扫描整个 r7 相同unit a/b/c下所有 1/2/3
                for r7_item_key in r7_item_keys:
                    r7_item_text = src_data[r7_item_key][2].strip().replace("\n","")
                    if r8_item_text == r7_item_text:
                        # 找到相同文本
                        if unit_pair_key in same_item_list:
                            same_item_list[unit_pair_key].append((r7_item_key, r8_item_key))
                        else:
                            same_item_list[unit_pair_key] = [(r7_item_key, r8_item_key)]
                        break
                    
    

In [52]:
same_item_list

{'r7_A_121.3_c|r8_A_121.3_c': [('r7_A_121.3_c_1', 'r8_A_121.3_c_1'),
  ('r7_A_121.3_c_2', 'r8_A_121.3_c_2')],
 'r7_A_121.9_d|r8_A_121.9_d': [('r7_A_121.9_d_1', 'r8_A_121.9_d_1'),
  ('r7_A_121.9_d_3', 'r8_A_121.9_d_3'),
  ('r7_A_121.9_d_4', 'r8_A_121.9_d_4'),
  ('r7_A_121.9_d_5', 'r8_A_121.9_d_5'),
  ('r7_A_121.9_d_6', 'r8_A_121.9_d_6'),
  ('r7_A_121.9_d_7', 'r8_A_121.9_d_7')],
 'r7_B_121.21_a|r8_B_121.21_a': [('r7_B_121.21_a_1', 'r8_B_121.21_a_1'),
  ('r7_B_121.21_a_2', 'r8_B_121.21_a_2'),
  ('r7_B_121.21_a_3', 'r8_B_121.21_a_3'),
  ('r7_B_121.21_a_4', 'r8_B_121.21_a_4'),
  ('r7_B_121.21_a_5', 'r8_B_121.21_a_5'),
  ('r7_B_121.21_a_6', 'r8_B_121.21_a_6')],
 'r7_B_121.23_b|r8_B_121.23_b': [('r7_B_121.23_b_1', 'r8_B_121.23_b_1')],
 'r7_B_121.23_a|r8_B_121.23_a': [('r7_B_121.23_a_1', 'r8_B_121.23_a_1'),
  ('r7_B_121.23_a_2', 'r8_B_121.23_a_2')],
 'r7_B_121.25_a|r8_B_121.25_a': [('r7_B_121.25_a_1', 'r8_B_121.25_a_1'),
  ('r7_B_121.25_a_3', 'r8_B_121.25_a_3'),
  ('r7_B_121.25_a_4', 'r8_B_121

In [53]:
# 对于同一unit内，所有item - 完全一样的item - 对的上的(相似度高) = 对不上的item(差异点)

# simi_pair_item_list = []

# 不能进一步拆分到1/2/3, 需要补充的 差异的部分
r7_unpair_unit_list_additional = {}
r8_unpair_unit_list_additional = {}

pair_item_list = {} # r7_unit_key|r8_unit_key : [(r7_item_key, r8_item_key),...]
r7_unpair_item_list = {} # r7_unit_key : [r7_item_keys]
r8_unpair_item_list = {} # r8_unit_key : [r8_item_keys]

for section in pair_unit_list:
    pair_units_in_section = pair_unit_list[section]
    for unit_pair in pair_units_in_section:
        r7_unit_key = unit_pair[0]
        r8_unit_key = unit_pair[1]
        unit_pair_score = unit_pair[2]
        unit_pair_key = f'{r7_unit_key}|{r8_unit_key}' # 对得上的unit_pair 新的key
        # 尝试取出同一 unit 下面所有的 1/2/3
        r7_item_keys = r7_unit_map_item_keys[r7_unit_key] if r7_unit_key in r7_unit_map_item_keys else []
        r8_item_keys = r8_unit_map_item_keys[r8_unit_key] if r8_unit_key in r8_unit_map_item_keys else []

        # 一开始 全部记为对不上
        r7_unpair_item_list[r7_unit_key] = r7_item_keys.copy()
        r8_unpair_item_list[r8_unit_key] = r8_item_keys.copy()

        # 如果都不能拆分到 1/2/3，需要根据a/b/c相似度得分, <0.9, 标记为 '有差异'
        if len(r7_item_keys) == 0 and len(r8_item_keys) == 0:
            if unit_pair_score < 0.9: 
                # 补充 r7
                if section in r7_unpair_unit_list_additional:
                    r7_unpair_unit_list_additional[section].append(r7_unit_key)
                else:
                    r7_unpair_unit_list_additional[section] = [r7_unit_key]
                # 补充 r8
                if section in r8_unpair_unit_list_additional:
                    r8_unpair_unit_list_additional[section].append(r8_unit_key)
                else:
                    r8_unpair_unit_list_additional[section] = [r8_unit_key]
        
        # 确认都可以进一步分解到 1/2/3，才需要进一步对比 1/2/3 的内容
        if len(r7_item_keys) > 0 and len(r8_item_keys) > 0:
            # 排除掉完全相同的 1/2/3
            if unit_pair_key in same_item_list:
                r7_same_items = [tup[0] for tup in same_item_list[unit_pair_key]]
                r8_same_items = [tup[1] for tup in same_item_list[unit_pair_key]]
                r7_remain_items = [item for item in r7_item_keys if item not in r7_same_items]
                r8_remain_items = [item for item in r8_item_keys if item not in r8_same_items]
            else:
                r7_remain_items = r7_item_keys.copy()
                r8_remain_items = r8_item_keys.copy()
            # 剩余同一 a/b/c 下所有 不完全相同的 1/2/3 交叉计算相似度
            items_simi_res = cross_cal_similarity(src_data, r7_remain_items, r8_remain_items)
            
            # 先保存匹配结果，进一步手工确认阈值 (最终阈值 下限0.6, 上限0.8)
            # for pair_item in items_simi_res:
            #     r7_item_text = src_data[pair_item[0]][2]
            #     r8_item_text = src_data[pair_item[1]][2]
            #     simi_pair_item_list.append((pair_item[0], pair_item[1], pair_item[2], r7_item_text, r8_item_text))
    
            r7_paired_items = []
            r8_paired_items = []
            for pair_item in items_simi_res:
                r7_item_key = pair_item[0]
                r8_item_key = pair_item[1]
                item_simi_score = pair_item[2]
                
                # 保存 对上了的item
                if item_simi_score > 0.7:
                    r7_paired_items.append(r7_item_key)
                    r8_paired_items.append(r8_item_key)
                    if unit_pair_key in pair_item_list:
                        pair_item_list[unit_pair_key].append((r7_item_key, r8_item_key, item_simi_score))
                    else:
                        pair_item_list[unit_pair_key] = [(r7_item_key, r8_item_key, item_simi_score)]
    
            # 各自所有 - 完全相同 - 对上了的 = 对不上的（不需要进一步拆分再比较）
            r7_unpaired_items = [item for item in r7_remain_items if item not in r7_paired_items]
            r8_unpaired_items = [item for item in r8_remain_items if item not in r8_paired_items]
            r7_unpair_item_list[r7_unit_key] = r7_unpaired_items.copy()
            r8_unpair_item_list[r8_unit_key] = r8_unpaired_items.copy()
        

In [54]:
# print(len(simi_pair_item_list))

# # 先保存到本地excel
# import pandas as pd

# df = pd.DataFrame(simi_pair_item_list, columns=['r7_item_key', 'r8_item_key', 'simi_score', 'r7_item_text', 'r8_item_text'])
# df.to_excel('item_pair_result.xlsx', index=False)

In [55]:
r7_unpair_unit_list_additional

{'121.131': ['r7_G_121.131_c'],
 '121.133': ['r7_G_121.133_d'],
 '121.171': ['r7_I_121.171_a'],
 '121.354': ['r7_K_121.354_a'],
 '121.359': ['r7_K_121.359_b', 'r7_K_121.359_e'],
 '121.362': ['r7_L_121.362_b', 'r7_L_121.362_a', 'r7_L_121.362_c'],
 '121.368': ['r7_L_121.368_c'],
 '121.379': ['r7_L_121.379_a'],
 '121.501': ['r7_Q_121.501_e'],
 '121.504': ['r7_R_121.504_a'],
 '121.505': ['r7_R_121.505_b'],
 '121.506': ['r7_R_121.506_a'],
 '121.508': ['r7_R_121.508_e', 'r7_R_121.508_c', 'r7_R_121.508_a'],
 '121.509': ['r7_R_121.509_d'],
 '121.511': ['r7_R_121.511_c', 'r7_R_121.511_d', 'r7_R_121.511_e'],
 '121.513': ['r7_R_121.513_c'],
 '121.531': ['r7_T_121.531_a'],
 '121.550': ['r7_T_121.550_b'],
 '121.711': ['r7_W_121.711_c', 'r7_W_121.711_e', 'r7_W_121.711_d']}

In [56]:
r8_unpair_unit_list_additional

{'121.131': ['r8_G_121.131_c'],
 '121.133': ['r8_G_121.133_d'],
 '121.171': ['r8_I_121.171_a'],
 '121.354': ['r8_K_121.354_a'],
 '121.359': ['r8_K_121.359_c', 'r8_K_121.359_e'],
 '121.362': ['r8_L_121.362_b', 'r8_L_121.362_a', 'r8_L_121.362_c'],
 '121.368': ['r8_L_121.368_c'],
 '121.379': ['r8_L_121.379_a'],
 '121.501': ['r8_Q_121.501_f'],
 '121.504': ['r8_R_121.504_a'],
 '121.505': ['r8_R_121.505_b'],
 '121.506': ['r8_R_121.506_a'],
 '121.508': ['r8_R_121.508_e', 'r8_R_121.508_c', 'r8_R_121.508_a'],
 '121.509': ['r8_R_121.509_d'],
 '121.511': ['r8_R_121.511_c', 'r8_R_121.511_d', 'r8_R_121.511_e'],
 '121.513': ['r8_R_121.513_c'],
 '121.531': ['r8_T_121.531_a'],
 '121.550': ['r8_T_121.550_b'],
 '121.711': ['r8_W_121.711_c', 'r8_W_121.711_e', 'r8_W_121.711_d']}

In [57]:
pair_item_list

{'r7_A_121.3_c|r8_A_121.3_c': [('r7_A_121.3_c_3',
   'r8_A_121.3_c_3',
   0.9976194214545906)],
 'r7_A_121.3_a|r8_A_121.3_a': [('r7_A_121.3_a_2',
   'r8_A_121.3_a_2',
   0.9744059904169099),
  ('r7_A_121.3_a_1', 'r8_A_121.3_a_1', 0.9569706523358513),
  ('r7_A_121.3_a_3', 'r8_A_121.3_a_3', 0.9541364379934263)],
 'r7_A_121.9_d|r8_A_121.9_d': [('r7_A_121.9_d_2',
   'r8_A_121.9_d_2',
   0.972896393036785)],
 'r7_B_121.23_b|r8_B_121.23_b': [('r7_B_121.23_b_3',
   'r8_B_121.23_b_3',
   0.9846186833703067),
  ('r7_B_121.23_b_2', 'r8_B_121.23_b_2', 0.9826362870272906)],
 'r7_B_121.23_a|r8_B_121.23_a': [('r7_B_121.23_a_3',
   'r8_B_121.23_a_4',
   0.9823576853766449)],
 'r7_B_121.25_a|r8_B_121.25_a': [('r7_B_121.25_a_2',
   'r8_B_121.25_a_2',
   0.9457557738857576)],
 'r7_B_121.25_b|r8_B_121.25_b': [('r7_B_121.25_b_8',
   'r8_B_121.25_b_8',
   1.0000000000000002),
  ('r7_B_121.25_b_4', 'r8_B_121.25_b_4', 0.9872702503443347),
  ('r7_B_121.25_b_1', 'r8_B_121.25_b_1', 0.9716434737822802)],
 'r7_B_

In [58]:
r7_unpair_item_list

{'r7_A_121.3_c': [],
 'r7_A_121.3_a': [],
 'r7_A_121.5_a': [],
 'r7_A_121.7_d': [],
 'r7_A_121.7_c': [],
 'r7_A_121.7_e': [],
 'r7_A_121.7_b': [],
 'r7_A_121.7_a': [],
 'r7_A_121.9_d': [],
 'r7_A_121.9_b': [],
 'r7_A_121.9_a': [],
 'r7_B_121.20_b': [],
 'r7_B_121.21_a': [],
 'r7_B_121.21_e': [],
 'r7_B_121.21_d': [],
 'r7_B_121.23_b': [],
 'r7_B_121.23_a': [],
 'r7_B_121.25_a': [],
 'r7_B_121.25_b': [],
 'r7_B_121.27_c': [],
 'r7_B_121.27_b': [],
 'r7_B_121.27_a': [],
 'r7_B_121.31_b': [],
 'r7_B_121.31_c': [],
 'r7_B_121.31_a': [],
 'r7_B_121.33_b': [],
 'r7_B_121.33_a': [],
 'r7_B_121.35_c': [],
 'r7_B_121.35_a': [],
 'r7_B_121.35_d': [],
 'r7_B_121.35_e': [],
 'r7_B_121.35_b': [],
 'r7_C_121.41_c': [],
 'r7_C_121.41_e': [],
 'r7_C_121.41_b': [],
 'r7_C_121.42_b': [],
 'r7_C_121.42_c': [],
 'r7_C_121.43_b': [],
 'r7_C_121.43_d': [],
 'r7_C_121.43_a': [],
 'r7_C_121.45_a': [],
 'r7_C_121.45_c': [],
 'r7_C_121.45_b': [],
 'r7_C_121.45_f': [],
 'r7_C_121.45_d': [],
 'r7_C_121.45_e': ['r

In [59]:
r8_unpair_item_list

{'r8_A_121.3_c': [],
 'r8_A_121.3_a': [],
 'r8_A_121.5_a': [],
 'r8_A_121.7_d': [],
 'r8_A_121.7_c': [],
 'r8_A_121.7_e': [],
 'r8_A_121.7_b': [],
 'r8_A_121.7_a': [],
 'r8_A_121.9_d': [],
 'r8_A_121.9_b': [],
 'r8_A_121.9_a': [],
 'r8_B_121.20_b': [],
 'r8_B_121.21_a': [],
 'r8_B_121.21_e': [],
 'r8_B_121.21_d': [],
 'r8_B_121.23_b': [],
 'r8_B_121.23_a': ['r8_B_121.23_a_3', 'r8_B_121.23_a_5'],
 'r8_B_121.25_a': [],
 'r8_B_121.25_b': [],
 'r8_B_121.27_c': [],
 'r8_B_121.27_b': [],
 'r8_B_121.27_a': [],
 'r8_B_121.31_b': [],
 'r8_B_121.31_c': [],
 'r8_B_121.31_a': [],
 'r8_B_121.33_b': [],
 'r8_B_121.33_a': [],
 'r8_B_121.35_c': [],
 'r8_B_121.35_a': [],
 'r8_B_121.35_d': [],
 'r8_B_121.35_e': [],
 'r8_B_121.35_b': [],
 'r8_C_121.41_c': [],
 'r8_C_121.41_e': [],
 'r8_C_121.41_b': [],
 'r8_C_121.42_b': [],
 'r8_C_121.42_c': [],
 'r8_C_121.43_b': [],
 'r8_C_121.43_d': [],
 'r8_C_121.43_a': ['r8_C_121.43_a_1'],
 'r8_C_121.45_b': [],
 'r8_C_121.45_d': [],
 'r8_C_121.45_c': [],
 'r8_C_121.4

In [60]:
# 对于对上了的 item，继续拆分到下一级，再进行一轮比较

# 对于可以拆分到‘roman’的部分， 生成 item : [roman]的映射
r7_item_map_roman_keys = {}
r8_item_map_roman_keys = {}

for key in src_data:
    if src_data[key][0] == 'roman':
        doc = key.split('_')[0]
        chapter = key.split('_')[1]
        section = key.split('_')[2]
        unit = key.split('_')[3]
        item = key.split('_')[4]
        roman = key.split('_')[5]
        item_path = f'{doc}_{chapter}_{section}_{unit}_{item}'
        if doc == 'r7':
            if item_path in r7_item_map_roman_keys:
                r7_item_map_roman_keys[item_path].append(key)
            else:
                r7_item_map_roman_keys[item_path] = [key]
        else:
            if item_path in r8_item_map_roman_keys:
                r8_item_map_roman_keys[item_path].append(key)
            else:
                r8_item_map_roman_keys[item_path] = [key]
    
    

In [61]:
print(len(r7_item_map_roman_keys))
print(len(r8_item_map_roman_keys))

94
98


In [62]:
r7_item_map_roman_keys

{'r7_B_121.35_b_3': ['r7_B_121.35_b_3_i',
  'r7_B_121.35_b_3_ii',
  'r7_B_121.35_b_3_iii'],
 'r7_B_121.35_b_4': ['r7_B_121.35_b_4_i', 'r7_B_121.35_b_4_ii'],
 'r7_B_121.35_c_1': ['r7_B_121.35_c_1_i',
  'r7_B_121.35_c_1_ii',
  'r7_B_121.35_c_1_iii',
  'r7_B_121.35_c_1_iv',
  'r7_B_121.35_c_1_v'],
 'r7_B_121.35_c_3': ['r7_B_121.35_c_3_i',
  'r7_B_121.35_c_3_ii',
  'r7_B_121.35_c_3_iii'],
 'r7_C_121.43_d_2': ['r7_C_121.43_d_2_i',
  'r7_C_121.43_d_2_ii',
  'r7_C_121.43_d_2_iii',
  'r7_C_121.43_d_2_iv',
  'r7_C_121.43_d_2_v'],
 'r7_C_121.45_a_2': ['r7_C_121.45_a_2_i',
  'r7_C_121.45_a_2_ii',
  'r7_C_121.45_a_2_iii'],
 'r7_E_121.95_b_1': ['r7_E_121.95_b_1_i',
  'r7_E_121.95_b_1_ii',
  'r7_E_121.95_b_1_iii',
  'r7_E_121.95_b_1_iv',
  'r7_E_121.95_b_1_v'],
 'r7_E_121.95_b_2': ['r7_E_121.95_b_2_i',
  'r7_E_121.95_b_2_ii',
  'r7_E_121.95_b_2_iii',
  'r7_E_121.95_b_2_iv'],
 'r7_E_121.95_b_3': ['r7_E_121.95_b_3_i',
  'r7_E_121.95_b_3_ii',
  'r7_E_121.95_b_3_iii'],
 'r7_E_121.95_b_4': ['r7_E_121.95_

In [63]:
# 所有能对得上的 item 继续比较
# 首先获得所有相同的 roman 的部分
same_roman_list = {} # r7_item_key|r8_item_key : [(r7_roman_key, r8_roman_key),...]

for pair_unit in pair_item_list:
    pair_items_in_pair_unit = pair_item_list[pair_unit]
    for item_pair in pair_items_in_pair_unit:
        r7_item_key = item_pair[0]
        r8_item_key = item_pair[1]
        item_pair_key = f'{r7_item_key}|{r8_item_key}' # 对得上的 item_pair 新的key
        # 尝试取出同一 item(1/2/3) 下面所有的 roman
        r7_roman_keys = r7_item_map_roman_keys[r7_item_key] if r7_item_key in r7_item_map_roman_keys else []
        r8_roman_keys = r8_item_map_roman_keys[r8_item_key] if r8_item_key in r8_item_map_roman_keys else []
        # print(r7_roman_keys)
        # print(r8_roman_keys)
        # print()
    
        # 确认都可以进一步分解到 roman，才需要进一步对比
        if len(r7_roman_keys) > 0 and len(r8_roman_keys) > 0:
            # 尝试对比同一roman的内容是否完全相同
            # 尝试取出 相同roman的 内容完全相同的 roman_key
            for r8_roman_key in r8_roman_keys:
                r8_roman_text = src_data[r8_roman_key][2].strip().replace("\n","")
                # 扫描整个 r7 相同item 1/2/3下所有 roman
                for r7_roman_key in r7_roman_keys:
                    r7_roman_text = src_data[r7_roman_key][2].strip().replace("\n","")
                    if r8_roman_text == r7_roman_text:
                        # 找到相同文本
                        if item_pair_key in same_roman_list:
                            same_roman_list[item_pair_key].append((r7_roman_key, r8_roman_key))
                        else:
                            same_roman_list[item_pair_key] = [(r7_roman_key, r8_roman_key)]
                        break
                    
    

In [64]:
same_roman_list

{'r7_B_121.35_c_1|r8_B_121.35_c_1': [('r7_B_121.35_c_1_i',
   'r8_B_121.35_c_1_i'),
  ('r7_B_121.35_c_1_iii', 'r8_B_121.35_c_1_iii'),
  ('r7_B_121.35_c_1_iv', 'r8_B_121.35_c_1_iv'),
  ('r7_B_121.35_c_1_v', 'r8_B_121.35_c_1_v')],
 'r7_B_121.35_c_3|r8_B_121.35_c_3': [('r7_B_121.35_c_3_i',
   'r8_B_121.35_c_3_i'),
  ('r7_B_121.35_c_3_ii', 'r8_B_121.35_c_3_ii')],
 'r7_C_121.45_a_2|r8_C_121.45_b_2': [('r7_C_121.45_a_2_i',
   'r8_C_121.45_b_2_i'),
  ('r7_C_121.45_a_2_iii', 'r8_C_121.45_b_2_iii')],
 'r7_E_121.95_b_2|r8_E_121.95_b_2': [('r7_E_121.95_b_2_i',
   'r8_E_121.95_b_2_i'),
  ('r7_E_121.95_b_2_iii', 'r8_E_121.95_b_2_iii'),
  ('r7_E_121.95_b_2_iv', 'r8_E_121.95_b_2_iv')],
 'r7_E_121.95_b_1|r8_E_121.95_b_1': [('r7_E_121.95_b_1_i',
   'r8_E_121.95_b_1_i'),
  ('r7_E_121.95_b_1_iii', 'r8_E_121.95_b_1_v'),
  ('r7_E_121.95_b_1_iv', 'r8_E_121.95_b_1_vi'),
  ('r7_E_121.95_b_1_v', 'r8_E_121.95_b_1_vii')],
 'r7_E_121.95_b_6|r8_E_121.95_b_6': [('r7_E_121.95_b_6_ii',
   'r8_E_121.95_b_6_ii')],
 'r7

In [65]:
# 对于配对的item内，所有roman - 完全一样的roman - 对的上的(相似度高) = 对不上的roman(差异点)

# simi_pair_roman_list = []

# 不能进一步拆分到roman, 需要补充的 差异的 item 部分
r7_unpair_item_list_additional = {}
r8_unpair_item_list_additional = {}

pair_roman_list = {} # r7_item_key|r8_item_key : [(r7_roman_key, r8_roman_key),...]
r7_unpair_roman_list = {} # r7_item_key : [r7_roman_keys]
r8_unpair_roman_list = {} # r8_item_key : [r8_roman_keys]

for pair_unit in pair_item_list:
    pair_items_in_pair_unit = pair_item_list[pair_unit]
    r7_unit_key = pair_unit.split('|')[0]
    r8_unit_key = pair_unit.split('|')[1]
    for item_pair in pair_items_in_pair_unit:
        r7_item_key = item_pair[0]
        r8_item_key = item_pair[1]
        item_pair_score = item_pair[2]
        item_pair_key = f'{r7_item_key}|{r8_item_key}' # 对得上的item_pair 新的key
        # 尝试取出同一 item 下面所有的 roman
        r7_roman_keys = r7_item_map_roman_keys[r7_item_key] if r7_item_key in r7_item_map_roman_keys else []
        r8_roman_keys = r8_item_map_roman_keys[r8_item_key] if r8_item_key in r8_item_map_roman_keys else []

        # 一开始 全部记为对不上
        r7_unpair_roman_list[r7_item_key] = r7_roman_keys.copy()
        r8_unpair_roman_list[r8_item_key] = r8_roman_keys.copy()

        # 如果两个 1/2/3 都不能拆分到 roman，需要根据1/2/3相似度得分, <0.8, 标记为 '有差异'
        if len(r7_roman_keys) == 0 and len(r8_roman_keys) == 0:
            if item_pair_score < 0.8: 
                # 补充 r7
                if r7_unit_key in r7_unpair_item_list_additional:
                    r7_unpair_item_list_additional[r7_unit_key].append(r7_item_key)
                else:
                    r7_unpair_item_list_additional[r7_unit_key] = [r7_item_key]
                # 补充 r8
                if r8_unit_key in r8_unpair_item_list_additional:
                    r8_unpair_item_list_additional[r8_unit_key].append(r8_item_key)
                else:
                    r8_unpair_item_list_additional[r8_unit_key] = [r8_item_key]
        
        # 确认都可以进一步分解到 roman，才需要进一步对比 roman 的内容
        if len(r7_roman_keys) > 0 and len(r8_roman_keys) > 0:
            # 排除掉完全相同的 roman
            if item_pair_key in same_roman_list:
                r7_same_romans = [tup[0] for tup in same_roman_list[item_pair_key]]
                r8_same_romans = [tup[1] for tup in same_roman_list[item_pair_key]]
                r7_remain_romans = [roman for roman in r7_roman_keys if roman not in r7_same_romans]
                r8_remain_romans = [roman for roman in r8_roman_keys if roman not in r8_same_romans]
            else:
                r7_remain_romans = r7_roman_keys.copy()
                r8_remain_romans = r8_roman_keys.copy()
            # 剩余同一 1/2/3 下所有 不完全相同的 roman 交叉计算相似度
            roman_simi_res = cross_cal_similarity(src_data, r7_remain_romans, r8_remain_romans)
            
            # 先保存匹配结果，进一步手工确认阈值 (最终阈值 下限0.6, 上限0.8)
            # for pair_roman in roman_simi_res:
            #     r7_roman_text = src_data[pair_roman[0]][2]
            #     r8_roman_text = src_data[pair_roman[1]][2]
            #     simi_pair_roman_list.append((pair_roman[0], pair_roman[1], pair_roman[2], r7_roman_text, r8_roman_text))
    
            r7_paired_romans = []
            r8_paired_romans = []
            for pair_roman in roman_simi_res:
                r7_roman_key = pair_roman[0]
                r8_roman_key = pair_roman[1]
                roman_simi_score = pair_roman[2]
                
                # 保存 相似的roman
                if roman_simi_score > 0.7:
                    r7_paired_romans.append(r7_roman_key)
                    r8_paired_romans.append(r8_roman_key)
                    if item_pair_key in pair_roman_list:
                        pair_roman_list[item_pair_key].append((r7_roman_key, r8_roman_key, roman_simi_score))
                    else:
                        pair_roman_list[item_pair_key] = [(r7_roman_key, r8_roman_key, roman_simi_score)]
    
            # 各自所有 - 完全相同 - 对上了的 = 对不上的（不需要进一步拆分再比较）
            r7_unpaired_romans = [roman for roman in r7_remain_romans if roman not in r7_paired_romans]
            r8_unpaired_romans = [roman for roman in r8_remain_romans if roman not in r8_paired_romans]
            r7_unpair_roman_list[r7_item_key] = r7_unpaired_romans.copy()
            r8_unpair_roman_list[r8_item_key] = r8_unpaired_romans.copy()
        

In [66]:
# print(len(simi_pair_roman_list))

# # 先保存到本地excel
# import pandas as pd

# df = pd.DataFrame(simi_pair_roman_list, columns=['r7_roman_key', 'r8_roman_key', 'simi_score', 'r7_roman_text', 'r8_roman_text'])
# df.to_excel('roman_pair_result.xlsx', index=False)

In [67]:
r7_unpair_item_list_additional

{'r7_G_121.131_b': ['r7_G_121.131_b_4'],
 'r7_G_121.133_b': ['r7_G_121.133_b_1'],
 'r7_G_121.133_a': ['r7_G_121.133_a_37',
  'r7_G_121.133_a_39',
  'r7_G_121.133_a_30',
  'r7_G_121.133_a_42'],
 'r7_H_121.157_a': ['r7_H_121.157_a_1'],
 'r7_I_121.195_b': ['r7_I_121.195_b_1'],
 'r7_K_121.309_b': ['r7_K_121.309_b_3'],
 'r7_K_121.309_c': ['r7_K_121.309_c_1'],
 'r7_K_121.354_b': ['r7_K_121.354_b_2'],
 'r7_L_121.366_c': ['r7_L_121.366_c_6'],
 'r7_O_121.457_d': ['r7_O_121.457_d_2'],
 'r7_R_121.508_b': ['r7_R_121.508_b_1'],
 'r7_R_121.510_d': ['r7_R_121.510_d_2'],
 'r7_R_121.510_b': ['r7_R_121.510_b_2'],
 'r7_R_121.510_e': ['r7_R_121.510_e_2'],
 'r7_R_121.515_a': ['r7_R_121.515_a_3'],
 'r7_R_121.515_b': ['r7_R_121.515_b_2']}

In [68]:
r8_unpair_item_list_additional

{'r8_G_121.131_b': ['r8_G_121.131_b_4'],
 'r8_G_121.133_b': ['r8_G_121.133_b_1'],
 'r8_G_121.133_a': ['r8_G_121.133_a_37',
  'r8_G_121.133_a_39',
  'r8_G_121.133_a_30',
  'r8_G_121.133_a_44'],
 'r8_H_121.157_a': ['r8_H_121.157_a_1'],
 'r8_I_121.195_b': ['r8_I_121.195_b_1'],
 'r8_K_121.309_b': ['r8_K_121.309_b_3'],
 'r8_K_121.309_c': ['r8_K_121.309_c_1'],
 'r8_K_121.354_c': ['r8_K_121.354_c_2'],
 'r8_L_121.366_c': ['r8_L_121.366_c_6'],
 'r8_O_121.457_d': ['r8_O_121.457_d_1'],
 'r8_R_121.508_b': ['r8_R_121.508_b_1'],
 'r8_R_121.510_c': ['r8_R_121.510_c_2'],
 'r8_R_121.510_b': ['r8_R_121.510_b_2'],
 'r8_R_121.510_d': ['r8_R_121.510_d_2'],
 'r8_R_121.515_a': ['r8_R_121.515_a_2'],
 'r8_R_121.515_b': ['r8_R_121.515_b_2']}

In [69]:
pair_roman_list

{'r7_B_121.35_c_1|r8_B_121.35_c_1': [('r7_B_121.35_c_1_ii',
   'r8_B_121.35_c_1_ii',
   0.9269430114370808)],
 'r7_B_121.35_c_3|r8_B_121.35_c_3': [('r7_B_121.35_c_3_iii',
   'r8_B_121.35_c_3_iii',
   0.998543955032229)],
 'r7_B_121.35_b_3|r8_B_121.35_b_3': [('r7_B_121.35_b_3_ii',
   'r8_B_121.35_b_3_ii',
   0.8870808901841225),
  ('r7_B_121.35_b_3_i', 'r8_B_121.35_b_3_i', 0.8759937429029582),
  ('r7_B_121.35_b_3_iii', 'r8_B_121.35_b_3_iii', 0.701118981294527)],
 'r7_B_121.35_b_4|r8_B_121.35_b_4': [('r7_B_121.35_b_4_ii',
   'r8_B_121.35_b_4_ii',
   0.9907438411039661)],
 'r7_C_121.45_a_2|r8_C_121.45_b_2': [('r7_C_121.45_a_2_ii',
   'r8_C_121.45_b_2_ii',
   0.8178515218554501)],
 'r7_E_121.95_b_2|r8_E_121.95_b_2': [('r7_E_121.95_b_2_ii',
   'r8_E_121.95_b_2_ii',
   0.7009405353548531)],
 'r7_E_121.95_b_6|r8_E_121.95_b_6': [('r7_E_121.95_b_6_i',
   'r8_E_121.95_b_6_i',
   0.877631091056729)],
 'r7_F_121.117_b_6|r8_F_121.117_b_6': [('r7_F_121.117_b_6_i',
   'r8_F_121.117_b_6_i',
   0.87763

In [70]:
r7_unpair_roman_list

{'r7_A_121.3_c_3': [],
 'r7_A_121.3_a_2': [],
 'r7_A_121.3_a_1': [],
 'r7_A_121.3_a_3': [],
 'r7_A_121.9_d_2': [],
 'r7_B_121.23_b_3': [],
 'r7_B_121.23_b_2': [],
 'r7_B_121.23_a_3': [],
 'r7_B_121.25_a_2': [],
 'r7_B_121.25_b_8': [],
 'r7_B_121.25_b_4': [],
 'r7_B_121.25_b_1': [],
 'r7_B_121.27_b_4': [],
 'r7_B_121.27_b_1': [],
 'r7_B_121.27_b_3': [],
 'r7_B_121.27_b_2': [],
 'r7_B_121.27_a_2': [],
 'r7_B_121.31_b_1': [],
 'r7_B_121.31_a_2': [],
 'r7_B_121.35_c_1': [],
 'r7_B_121.35_c_3': [],
 'r7_B_121.35_c_5': [],
 'r7_B_121.35_c_2': [],
 'r7_B_121.35_c_4': [],
 'r7_B_121.35_a_1': [],
 'r7_B_121.35_a_2': [],
 'r7_B_121.35_d_1': [],
 'r7_B_121.35_d_2': [],
 'r7_B_121.35_d_3': [],
 'r7_B_121.35_e_2': [],
 'r7_B_121.35_b_2': [],
 'r7_B_121.35_b_3': [],
 'r7_B_121.35_b_4': ['r7_B_121.35_b_4_i'],
 'r7_C_121.41_b_2': [],
 'r7_C_121.43_d_1': [],
 'r7_C_121.43_a_2': [],
 'r7_C_121.43_a_4': [],
 'r7_C_121.43_a_3': [],
 'r7_C_121.43_a_5': [],
 'r7_C_121.43_a_1': [],
 'r7_C_121.43_a_6': [],
 '

In [71]:
r8_unpair_roman_list

{'r8_A_121.3_c_3': [],
 'r8_A_121.3_a_2': [],
 'r8_A_121.3_a_1': [],
 'r8_A_121.3_a_3': [],
 'r8_A_121.9_d_2': [],
 'r8_B_121.23_b_3': [],
 'r8_B_121.23_b_2': [],
 'r8_B_121.23_a_4': [],
 'r8_B_121.25_a_2': [],
 'r8_B_121.25_b_8': [],
 'r8_B_121.25_b_4': [],
 'r8_B_121.25_b_1': [],
 'r8_B_121.27_b_4': [],
 'r8_B_121.27_b_1': [],
 'r8_B_121.27_b_3': [],
 'r8_B_121.27_b_2': [],
 'r8_B_121.27_a_2': [],
 'r8_B_121.31_b_1': [],
 'r8_B_121.31_a_2': [],
 'r8_B_121.35_c_1': [],
 'r8_B_121.35_c_3': [],
 'r8_B_121.35_c_5': [],
 'r8_B_121.35_c_2': [],
 'r8_B_121.35_c_4': [],
 'r8_B_121.35_a_1': [],
 'r8_B_121.35_a_2': [],
 'r8_B_121.35_d_1': [],
 'r8_B_121.35_d_2': [],
 'r8_B_121.35_d_3': [],
 'r8_B_121.35_e_2': [],
 'r8_B_121.35_b_2': [],
 'r8_B_121.35_b_3': [],
 'r8_B_121.35_b_4': ['r8_B_121.35_b_4_i'],
 'r8_C_121.41_b_2': [],
 'r8_C_121.43_d_1': [],
 'r8_C_121.43_a_3': [],
 'r8_C_121.43_a_5': [],
 'r8_C_121.43_a_4': [],
 'r8_C_121.43_a_6': [],
 'r8_C_121.43_a_2': [],
 'r8_C_121.43_a_7': [],
 '

In [56]:
# # 合并所有差异, 8 vs 7
# r7_final_marked_key = [] # [(level, key, change_type)]
# r8_final_marked_key = []

# # r7 多出来的 条
# for section in different_section_7_vs_8:
#     r7_final_marked_key.append(('section', section, '删除', '', '', '', ''))

# # r8 多出来的 条
# for section in different_section_8_vs_7:
#     r8_final_marked_key.append(('section', section, '新增', '', '', '', ''))

# # r7 和 r8 条 标题不同
# for section in different_section_title:
#     r7_final_marked_key.append(('section', section, '节标题更新', '', '', '', ''))
#     r8_final_marked_key.append(('section', section, '节标题更新', '', '', '', ''))

# # # r7 和 r8 条 头部正文不同
# for section in different_section_text:
#     r7_final_marked_key.append(('section', section, '节头部正文内容更新', '', '', '', ''))
#     r8_final_marked_key.append(('section', section, '节头部正文内容更新', '', '', '', ''))

# # r7 标记为不同的 a/b/c
# for section in r7_unpair_unit_list:
#     for unit in r7_unpair_unit_list[section]:
#         r7_final_marked_key.append(('unit', unit, '删除', '', '', '', ''))

# # r8 标记为不同的 a/b/c
# for section in r8_unpair_unit_list:
#     for unit in r8_unpair_unit_list[section]:
#         r8_final_marked_key.append(('unit', unit, '新增', '', '', '', ''))

# # r7 标记为不同的 1/2/3
# for unit in r7_unpair_item_list:
#     for item in r7_unpair_item_list[unit]:
#         r7_final_marked_key.append(('item', item, '删除', '', '', '', ''))

# # r8 标记为不同的 1/2/3
# for unit in r8_unpair_item_list:
#     for item in r8_unpair_item_list[unit]:
#         r8_final_marked_key.append(('item', item, '新增', '', '', '', ''))

# # r7 标记为不同的 i/ii/iii
# for item in r7_unpair_roman_list:
#     for roman in r7_unpair_roman_list[item]:
#         r7_final_marked_key.append(('roman', roman, '删除', '', '', '', ''))

# # r8 标记为不同的 i/ii/iii
# for item in r8_unpair_roman_list:
#     for roman in r8_unpair_roman_list[item]:
#         r8_final_marked_key.append(('roman', roman, '新增', '', '', '', ''))

# # r7 和 r8 配对 a/b/c
# for section in pair_unit_list:
#     for pair_unit in pair_unit_list[section]:
#         r7_final_marked_key.append(('unit', pair_unit[0], '变更', pair_unit[1], pair_unit[2], src_data[pair_unit[0]][2], src_data[pair_unit[1]][2]))
#         r8_final_marked_key.append(('unit', pair_unit[1], '变更', pair_unit[0], pair_unit[2], src_data[pair_unit[1]][2], src_data[pair_unit[0]][2]))

# # r7 和 r8 配对 1/2/3
# for pair_unit in pair_item_list:
#     for pair_item in pair_item_list[pair_unit]:
#         r7_final_marked_key.append(('item', pair_item[0], '变更', pair_item[1], pair_item[2], src_data[pair_item[0]][2], src_data[pair_item[1]][2]))
#         r8_final_marked_key.append(('item', pair_item[1], '变更', pair_item[0], pair_item[2], src_data[pair_item[1]][2], src_data[pair_item[0]][2]))

# # r7 和 r8 配对 i/ii/iv
# for pair_item in pair_roman_list:
#     for pair_roman in pair_roman_list[pair_item]:
#         r7_final_marked_key.append(('roman', pair_roman[0], '变更', pair_roman[1], pair_roman[2], src_data[pair_roman[0]][2], src_data[pair_roman[1]][2]))
#         r8_final_marked_key.append(('roman', pair_roman[1], '变更', pair_roman[0], pair_roman[2], src_data[pair_roman[1]][2], src_data[pair_roman[0]][2]))

In [57]:
# r7_final_marked_key

[('section', '121.175', '删除', '', '', '', ''),
 ('section', '121.177', '删除', '', '', '', ''),
 ('section', '121.179', '删除', '', '', '', ''),
 ('section', '121.181', '删除', '', '', '', ''),
 ('section', '121.183', '删除', '', '', '', ''),
 ('section', '121.185', '删除', '', '', '', ''),
 ('section', '121.187', '删除', '', '', '', ''),
 ('section', '121.327', '删除', '', '', '', ''),
 ('section', '121.331', '删除', '', '', '', ''),
 ('section', '121.343', '删除', '', '', '', ''),
 ('section', '121.708', '删除', '', '', '', ''),
 ('section', '121.713', '删除', '', '', '', ''),
 ('section', '121.727', '删除', '', '', '', ''),
 ('section', '121.21', '节标题更新', '', '', '', ''),
 ('section', '121.43', '节标题更新', '', '', '', ''),
 ('section', '121.49', '节标题更新', '', '', '', ''),
 ('section', '121.97', '节标题更新', '', '', '', ''),
 ('section', '121.103', '节标题更新', '', '', '', ''),
 ('section', '121.191', '节标题更新', '', '', '', ''),
 ('section', '121.193', '节标题更新', '', '', '', ''),
 ('section', '121.195', '节标题更新', '', '', ''

In [58]:
# r8_final_marked_key

[('section', '121.52', '新增', '', '', '', ''),
 ('section', '121.441', '新增', '', '', '', ''),
 ('section', '121.519', '新增', '', '', '', ''),
 ('section', '121.526', '新增', '', '', '', ''),
 ('section', '121.530', '新增', '', '', '', ''),
 ('section', '121.554', '新增', '', '', '', ''),
 ('section', '121.610', '新增', '', '', '', ''),
 ('section', '121.611', '新增', '', '', '', ''),
 ('section', '121.702', '新增', '', '', '', ''),
 ('section', '121.704', '新增', '', '', '', ''),
 ('section', '121.706', '新增', '', '', '', ''),
 ('section', '121.760', '新增', '', '', '', ''),
 ('section', '121.21', '节标题更新', '', '', '', ''),
 ('section', '121.43', '节标题更新', '', '', '', ''),
 ('section', '121.49', '节标题更新', '', '', '', ''),
 ('section', '121.97', '节标题更新', '', '', '', ''),
 ('section', '121.103', '节标题更新', '', '', '', ''),
 ('section', '121.191', '节标题更新', '', '', '', ''),
 ('section', '121.193', '节标题更新', '', '', '', ''),
 ('section', '121.195', '节标题更新', '', '', '', ''),
 ('section', '121.197', '节标题更新', '', '', 

In [62]:
# # qc 两个数组内没有重复的 key？
# print(len([tup[1] for tup in r7_final_marked_key if tup[0] != 'section']))
# print(len(set([tup[1] for tup in r7_final_marked_key if tup[0] != 'section'])))

1024
1024


In [63]:
# print(len([tup[1] for tup in r8_final_marked_key if tup[0] != 'section']))
# print(len(set([tup[1] for tup in r8_final_marked_key if tup[0] != 'section'])))

1032
1032


In [348]:
# # 保存到本地excel
# import pandas as pd

# df1 = pd.DataFrame(r7_final_marked_key, columns=['text_level', 'text_key', 'text_change_type', 'similar_text_key', 'similar_score', 'text_content', 'similar_text_content'])
# df1.to_excel('r7_marked_result.xlsx', index=False)

# df2 = pd.DataFrame(r8_final_marked_key, columns=['text_level', 'text_key', 'text_change_type', 'similar_text_key', 'similar_score', 'text_content', 'similar_text_content'])
# df2.to_excel('r8_marked_result.xlsx', index=False)

In [91]:
# prompt 变更的文本，分析差异的地方

from zhipuai import ZhipuAI

client = ZhipuAI(api_key="1b2d462c253146a98518bbfc0ba1b9cc.4UwLIcOT0PW0v43r")

def get_diff(r7_text, r8_text):
    completion = client.chat.completions.create(
      model="glm-4",
      temperature=0.5,
      messages=[
        {"role": "system", "content": "你是中国民航局的法规制定人员，你有非常专业的民航知识。你现在需要帮我处理一些民航法规文件的事情。"},
        {"role": "user", "content": f"请找出R7和R8两个版本相关民航法规文本的区别, 请侧重寻找语义的差异。\
         请忽略以下差异： \
         1.中英文符号差异；\
         2.'民航局'、'中国民航局'、'局方'无差异，'地区管理局'和'民航地区管理局'无差异；\
         3.数值格式的差异(是否包含千位分隔符)，比如'7500元'和'7,500元'无差异， '1100小时'和'1,100小时'无差异；\
         4.单位叫法差异，比如°和度无差异；\
         5.专用名词后面是否带缩写，'专业术语'和'专业术语(缩写字母)无差异', 例如 名词1 和 名词1(缩写1)无差异；\
         6.标点符号的差异，比如；和。无差异；\
         7.书写者的习惯，比如'设备'和'设施'无差异、'运营'和'运行'无差异; \
         8.'CCAR数字'和'CCAR-数字'无差异；\
         9.中文连接词表达的差异，'或'和'或者'无差异； \
         \
         如果文本中提到以下内容，在两段文本中出现差异，请列举出来：\
         1.条款引用差异，条款示例：P章、'第121.xx条'(这里xx代表数字)、(a)、(1)、(i)；\
         2.数值差异，只统计数值不相等的差异，(例如‘2200小时'和'2,200小时'无差异, 但是‘1100'和'1,200'有差异) 数字示例：15.2米、50英尺、15°、1001小时、'1,001小时'；\
         3.日期差异；\
         4.规章文件引用的差异，规章文件示例：《民用航空器驾驶员合格审定规则》； \
         5.主体对象差异，主体对象示例：机组成员，乘务员，合格证持有人，局方（指民航局），机长，飞机上的各种系统，各种飞机型号；\
         \
         请严格按照以下格式输出： \
         差异1：差异点（只考虑上面提到的内容） \
         R7： 提取差异的内容，不需要是一段完整的话。如果没有，直接输入无 \
         R8： 提取差异的内容，不需要是一段完整的话。如果没有，直接输入无 \
         差异2：差异点（只考虑上面提到的内容） \
         R7： 提取差异的内容，不需要是一段完整的话。如果没有，直接输入无 \
         R8： 提取差异的内容，不需要是一段完整的话。如果没有，直接输入无 \
         如果没有其他差异，请不要继续输出 \
         如果有其他差异，请输出：\
         其他差异：上面提到的内容之外的差异（尽量简短描述，请不要重复上面提到的差异点）\
         如果两段文字只存在开始提到的需要忽略的差异，请直接输出：无内容差异 \
         以下是文本内容：\
         R7版本：{r7_text} \
         R8版本：{r8_text}"
        }
      ]
    )
    diff_content = completion.choices[0].message.content
    print('------------------------------------------------------------')
    print(diff_content)
    return diff_content

In [92]:
test_text1 = """合格证持有人只能使用经局方认可的气象服务系统提供的气象资料。旅客。每个合格证持有人应当按照下列要求为旅客提供氧气：对于座舱气压高度 3000米(10000英尺)以上至 4300米(14000英尺)（含）的飞行，如果在这些高度上超过 30 分钟，则对于 30 分钟后的那段飞行应当为10％的旅客提供足够的氧气；对于座舱气压高度 4300米(14000英尺)以上至 4600米(15000英尺)（含）的飞行，足以为 30％的旅客在这些高度的飞行中提供氧气；对于座舱气压高度 4600 米(15000 英尺)以上的飞行，在此高度上整个飞行时间内为机上每一旅客提供足够的氧气。"""
test_text2 = """旅客。除经局方批准外，每个合格证持有人应当按照下列要求为旅客提供氧气：对于座舱气压高度 3,000 米(10,000 英尺)以上至 4,000米(13,000 英尺)(含)的飞行，如果在这些高度上超过 30 分钟，则对于 30 分钟后的那段飞行应当为 10％的旅客提供足够的氧气；对于座舱气压高度 4,000 米(13,000 英尺)以上的飞行，在此高度上整个飞行时间内为机上每一旅客提供足够的氧气。"""
test_diff = get_diff(test_text1, test_text2)

------------------------------------------------------------
差异1：条款引用差异
R7：无
R8：除经局方批准外

差异2：数值差异
R7：4300米(14000英尺)以上至 4600米(15000英尺)
R8：4,000 米(13,000 英尺)

差异3：规章要求范围差异
R7：对于座舱气压高度 3000米(10000英尺)以上至 4300米(14000英尺)（含）的飞行...对于座舱气压高度 4300米(14000英尺)以上至 4600米(15000英尺)（含）的飞行...对于座舱气压高度 4600 米(15000 英尺)以上的飞行
R8：对于座舱气压高度 3,000 米(10,000 英尺)以上至 4,000米(13,000 英尺)(含)的飞行...对于座舱气压高度 4,000 米(13,000 英尺)以上的飞行

其他差异：R8版本中删除了R7版本中4300米至4600米高度区间提供氧气的具体要求，同时更改了最高高度要求。

如果两段文字只存在需要忽略的差异，我的输出为：
无内容差异

但根据上述分析，这里存在上述列出的差异。


In [ ]:
# 合并到一个文件里面
final_res = [] # 'text_level', 'r7_text_key', 'text_change_type', 'r8_text_key', 'similar_score', 'r7_text_content', 'r8_text_content', 'diff'

# r7 多出来的 条
for section in different_section_7_vs_8:
    final_res.append(('section', section, '删除', '', '', '', '', ''))
# print(len(final_res))

# r8 多出来的 条
for section in different_section_8_vs_7:
    final_res.append(('section', '', '新增', section, '', '', '', ''))
# print(len(final_res))

# r7 和 r8 条 标题不同
for section in different_section_title:
    final_res.append(('section', section, '节标题更新', '', '', different_section_title[section][0], different_section_title[section][1], ''))
# print(len(final_res))

# # r7 和 r8 条 头部正文不同
for section in different_section_text:
    diff_content = ''
    if different_section_text[section][2] < 1:
        diff_content = get_diff(different_section_text[section][0], different_section_text[section][1])
    final_res.append(('section', section, '节头部正文内容更新', '', different_section_text[section][2], different_section_text[section][0], different_section_text[section][1], diff_content))
# print(len(final_res))

# r7 标记为不同的 a/b/c
for section in r7_unpair_unit_list:
    for unit in r7_unpair_unit_list[section]:
        final_res.append(('unit', unit, '删除', '', '', '', '', ''))
# print(len(final_res))

# r8 标记为不同的 a/b/c
for section in r8_unpair_unit_list:
    for unit in r8_unpair_unit_list[section]:
        final_res.append(('unit', '', '新增', unit, '', '', '', ''))
# print(len(final_res))

# r7 标记为不同的 1/2/3
for unit in r7_unpair_item_list:
    for item in r7_unpair_item_list[unit]:
        final_res.append(('item', item, '删除', '', '', '', '', ''))
# print(len(final_res))

# r8 标记为不同的 1/2/3
for unit in r8_unpair_item_list:
    for item in r8_unpair_item_list[unit]:
        final_res.append(('item', '', '新增', item, '', '', '', ''))
# print(len(final_res))

# r7 标记为不同的 i/ii/iii
for item in r7_unpair_roman_list:
    for roman in r7_unpair_roman_list[item]:
        final_res.append(('roman', roman, '删除', '', '', '', '', ''))
# print(len(final_res))

# r8 标记为不同的 i/ii/iii
for item in r8_unpair_roman_list:
    for roman in r8_unpair_roman_list[item]:
        final_res.append(('roman', '', '新增', roman, '', '', '', ''))
# print(len(final_res))

# r7 和 r8 配对 a/b/c
for section in pair_unit_list:
    for pair_unit in pair_unit_list[section]:
        diff_content = ''
        if pair_unit[2] < 1:
            diff_content = get_diff(src_data[pair_unit[0]][2], src_data[pair_unit[1]][2])
        final_res.append(('unit', pair_unit[0], '变更', pair_unit[1], pair_unit[2], src_data[pair_unit[0]][2], src_data[pair_unit[1]][2], diff_content))
# print(len(final_res))

# r7 和 r8 配对 1/2/3
for pair_unit in pair_item_list:
    for pair_item in pair_item_list[pair_unit]:
        diff_content = ''
        if pair_item[2] < 1:
            diff_content = get_diff(src_data[pair_item[0]][2], src_data[pair_item[1]][2])
        final_res.append(('item', pair_item[0], '变更', pair_item[1], pair_item[2], src_data[pair_item[0]][2], src_data[pair_item[1]][2], diff_content))
# print(len(final_res))

# r7 和 r8 配对 i/ii/iv
for pair_item in pair_roman_list:
    for pair_roman in pair_roman_list[pair_item]:
        diff_content = ''
        if pair_roman[2] < 1:
            diff_content = get_diff(src_data[pair_roman[0]][2], src_data[pair_roman[1]][2])
        final_res.append(('roman', pair_roman[0], '变更', pair_roman[1], pair_roman[2], src_data[pair_roman[0]][2], src_data[pair_roman[1]][2], diff_content))
# print(len(final_res))


------------------------------------------------------------
根据您的要求，以下是R7和R8两个版本相关民航法规文本的区别：

差异1：规章文件引用的差异
R7：无
R8：在《国务院对确需保留的行政审批项目设定行政许可的决定》后加入了逗号，

由于文本内容非常有限，且根据您的要求忽略了多种类型的差异，这里是唯一根据您的要求识别出的差异。如果文本内容更加详细或包含更多条款，可能能识别出更多的差异。

其他差异：无内容差异

请注意，这里提供的分析仅基于您提供的文本内容，如果存在更多的文本内容或更复杂的差异，可能需要进一步的审查和分析。
------------------------------------------------------------
差异1：规章文件引用的差异
R7：《民用航空器驾驶员合格审定规则》（CCAR61）、《一般运行和飞行规则》（CCAR91）
R8：《民用航空器驾驶员合格审定规则》(CCAR-61)、《一般运行和飞行规则》(CCAR-91)

差异2：条款引用差异
R7：无
R8：附件 2（应为“附件二”）

其他差异：数值差异（这里没有提到，但若文本其他部分出现此类情况，则需指出）

根据您提供的文本内容，以上是R7和R8版本之间的主要差异。如果文本其他部分存在其他提到的差异点，请相应地进行补充。根据您的要求，我已经忽略了其他不相关的差异。
------------------------------------------------------------
差异1：条款具体要求的表述差异
R7：无
R8：合格证持有人的飞机上应当携带运行合格证及其运行规范经认证的真实副本，并保证副本与正本一致。该副本可以是纸质版，也可以是符合局方要求的其他形式。

差异2：基地称谓的差异
R7：主运营基地
R8：主运行基地

其他差异：上述提到的内容之外的差异，以下是具体描述：
R8版本相较于R7版本，明确了飞机上携带的运行合格证及其运行规范复印件需为“经认证的真实副本”，并强调了副本需要与正本一致。同时，R8版本扩展了副本的形式，不仅限于纸质版，也可以是其他符合局方要求的形式。

如果两段文字只存在开始提到的需要忽略的差异，请直接输出：无内容差异
（但根据上述分析，这里存在需要关注的差

In [ ]:
# 保存到本地excel
import pandas as pd

df = pd.DataFrame(final_res, columns=['text_level', 'r7_text_key', 'text_change_type', 'r8_text_key', 'similar_score', 'r7_text_content', 'r8_text_content', 'diff_content'])
df.to_excel('r7_r8_marked_result.xlsx', index=False)
